In [ ]:
!pip3 install tokenizers --quiet
!pip install -U transformers --quiet
# !pip install vncorenlp --quiet
# !mkdir -p vncorenlp/models/wordsegmenter
# !wget --quiet https://raw.githubusercontent.com/vncorenlp/VnCoreNLP/master/VnCoreNLP-1.2.jar
# !wget --quiet https://raw.githubusercontent.com/vncorenlp/VnCoreNLP/master/models/wordsegmenter/vi-vocab
# !wget --quiet https://raw.githubusercontent.com/vncorenlp/VnCoreNLP/master/models/wordsegmenter/wordsegmenter.rdr
# !mv VnCoreNLP-1.2.jar vncorenlp/
# !mv vi-vocab vncorenlp/models/wordsegmenter/
# !mv wordsegmenter.rdr vncorenlp/models/wordsegmenter/
!pip install -U sentence-transformers --quiet
!pip install pyvi --quiet
!pip install rank_bm25 --quiet

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
from google.colab import files
import pandas as pd
import numpy as np
import json
import numpy

In [ ]:
file_path = "/content/drive/MyDrive/Colab Notebooks/DS/data/ise-dsc01-train_BEST.json"
df = pd.read_json(file_path, orient='index')

In [ ]:
import torch
from sentence_transformers import SentenceTransformer
from transformers import AutoModel, AutoTokenizer

# https://huggingface.co/keepitreal/vietnamese-sbert
# sbert_embedding_model = SentenceTransformer('keepitreal/vietnamese-sbert')

# https://github.com/vovanphuc/SimeCSE_Vietnamese
# không cần segment
# simcse_embedding_model = SentenceTransformer('VoVanPhuc/sup-SimCSE-VietNamese-phobert-base')




# PhobertTokenizer = AutoTokenizer.from_pretrained("VoVanPhuc/sup-SimCSE-VietNamese-phobert-base")
# model = AutoModel.from_pretrained("VoVanPhuc/sup-SimCSE-VietNamese-phobert-base")


In [ ]:
# tokenizer_phobert_large = AutoTokenizer.from_pretrained("vinai/phobert-large")
# phobert_large = AutoModel.from_pretrained("vinai/phobert-large")

In [ ]:
tokenizer_phobert_v2 = AutoTokenizer.from_pretrained("vinai/phobert-base-v2")
phobert_v2 = AutoModel.from_pretrained("vinai/phobert-base-v2", output_hidden_states=True)

Some weights of RobertaModel were not initialized from the model checkpoint at vinai/phobert-base-v2 and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
if torch.cuda.is_available():
    device = torch.device("cuda")
    print('There are %d GPU(s) available.' % torch.cuda.device_count())
    print('We will use the GPU:', torch.cuda.get_device_name(0))
else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")

There are 1 GPU(s) available.
We will use the GPU: Tesla T4


# Ranking

In [ ]:
from rank_bm25 import BM25Okapi, BM25Plus, BM25L

# Preprocess

In [ ]:
pip install underthesea

In [ ]:
import underthesea
from scipy.spatial.distance import cosine
import sys
import os
import re
import json
import numpy as np

def preprocess_text(text: str) -> str:
    text = re.sub(r"['\",\.\?:\-!]", "", text)
    text = text.strip()
    text = " ".join(text.split())
    text = text.lower()
    return text

def preprocess_text2(text: str) -> str:
    text = re.sub(r"['\"\.]", "", text)
    text = text.strip()
    text = " ".join(text.split())
    text = text.lower()
    return text

def move_punctuation_after_quotes(text):
    pattern = r'([.?!])(”)'
    result = re.sub(pattern, r'\2\1', text)
    return result

def split_context(text):
    # text = move_punctuation_after_quotes(text)
    punctuation_marks = r'(?<!St)(?<!TP)(?<!PGS)(?<!BS)(?<!GS)(?<!\.[A-Z])\.(?![0-9])(?![a-z])(?!\s*-)(?![A-Z])(?!\,)(?!”)|(\.\n\n)|(?<!\n)\n(?!\n)'
    # punctuation_marks = r'(?<!St)(?<!TP)(?<!PGS)(?<!BS)(?<!GS)(?<!\.[A-Z])\.(?![0-9])(?![a-z])(?!\s*-)(?![A-Z])(?!\,)(?!”)|\n'
    sentences = re.split(punctuation_marks, text)
    sentences = [sentence.strip() for sentence in sentences if sentence is not None and sentence.strip()]
    return sentences


def concat_segmented_text(text):
    s = ''
    for t in text:
        s += ' '.join(t)
    return s

In [ ]:
def preprocess(text):
  text = preprocess_text2(text)
  text = move_punctuation_after_quotes(text)

  text = str(text)\
    .replace(";", "").replace("“", "") \
    .replace(":", "").replace("”", "") \
    .replace('"', "").replace("'", "") \
    .replace("!", "").replace("?", "") \
    .replace("-", "")
  text = text.strip().lower()
  return text

# Call phoBert

In [ ]:
phobert_v2 = phobert_v2.to(device)

In [ ]:
def get_sentence_embedding(input):

    sentence = preprocess(input)

    line = underthesea.word_tokenize(sentence, format="text")
    # Tokenize câutokenizer_phobert_v2.encode(line)
    v_tokenized = tokenizer_phobert_v2.encode(line)

    max_len = 200
    # Chèn thêm số 1 vào cuối câu nếu như không đủ 100 từ
    padded = numpy.array([v_tokenized + [1] * (max_len - len(v_tokenized))])

    attention_mask = numpy.where(padded == 1, 0, 1)

    padded = torch.tensor(padded).to(torch.long)
    attention_mask = torch.tensor(attention_mask)


    padded = padded.to(device)
    attention_mask = attention_mask.to(device)

    # Lấy features dầu ra từ BERT
    with torch.no_grad():
        last_hidden_states = phobert_v2(input_ids= padded, attention_mask=attention_mask)

    v_features = last_hidden_states[0][:, 0, :]

    return v_features.flatten()

def calculate_cosine_similarity(sentence1_embedding, sentence2_embedding):

    # sentence2_embedding = get_sentence_embedding(sentence2)

    # Tính toán độ tương đồng cosine
    sentence1_embedding = sentence1_embedding.unsqueeze(0)
    sentence2_embedding = sentence2_embedding.unsqueeze(0)
    cosine_similarity = torch.nn.functional.cosine_similarity(sentence1_embedding, sentence2_embedding)

    return cosine_similarity.item()


In [ ]:
def jaccard_similarity(sentence1, sentence2):
    # sentence1 = preprocess(sentence1)
    # sentence2 = preprocess(sentence2)
    set1 = set(sentence1.split())
    set2 = set(sentence2.split())
    intersection = set1.intersection(set2)
    union = set1.union(set2)
    return len(intersection) / len(union)

def euclidean_distance(sentence1_embedding, sentence2_embedding):
    # Tính toán độ tương đồng cosine
    sentence1_embedding = sentence1_embedding.unsqueeze(0)
    sentence2_embedding = sentence2_embedding.unsqueeze(0)

    return torch.sqrt(torch.sum((sentence1_embedding - sentence2_embedding) ** 2))


## FindEvidence


In [ ]:
progress = 0

def FindEvidence(x, thres_value=None, top=5):
  global progress
  progress += 1
  print('#', progress)
  ids = [1]
  sorted_ctx_sents = []
  sorted_ctx_scores = []
  idxs = []
  # print(x)

  # ids.append(x.index[0])
  # chọn ra top các đoạn liên quan nhất trong x
  sents_of_ctx = split_context(str(x.context))
  tokenized_corpus = [doc.split(" ") for doc in sents_of_ctx]
  # Thay đổi hàm đo BM25 score ở đây
  bm25 = BM25Okapi(tokenized_corpus)
  query = str(x['claim'])
  tokenized_query = query.split(" ")
  doc_scores = bm25.get_scores(tokenized_query)
  sorted_ids = np.argsort(doc_scores, kind='mergesort')[::-1][:5]
  # print(str(x.evidence))
  value = 0.0
  if thres_value is not None:
      sorted_ctx_sents.append(np.array(sents_of_ctx)[sorted_ids[:thres_value]])
      sorted_ctx_scores.append(doc_scores[sorted_ids[:thres_value]])
      idxs.append(sorted_ids[:thres_value])
  elif thres_value is None:
      # thres_value = len(df)
      sorted_ctx_sents.append(np.array(sents_of_ctx)[sorted_ids])
      sorted_ctx_scores.append(doc_scores[sorted_ids])
      idxs.append(sorted_ids)


  QueryFeature = get_sentence_embedding(query)

  candidates = np.array(sents_of_ctx)[sorted_ids]
  # print(candidates)
  top = {}

  for idx, candidate in enumerate(candidates):
    q = preprocess(query)
    c = preprocess(str(candidate))
    CandidateFeature = get_sentence_embedding(str(candidate))
    top[str(candidate)] = calculate_cosine_similarity(QueryFeature, CandidateFeature) \
    + 0.07*sorted_ctx_scores[0][idx] \
    + 5*jaccard_similarity(q, c) \
    - 0.1*euclidean_distance(QueryFeature, CandidateFeature)


  sorted_dict = {k: v for k, v in sorted(top.items(), key=lambda item: item[1], reverse=True)}

  # print(sorted_dict)
  # print('___________________________________________________________________________________')


  return list(ids), list(sorted_ctx_sents), list(sorted_ctx_scores), list(idxs), sorted_dict

In [ ]:
## 500 evi

# 348
# 388 mahatan
# 389 mahatan x2
# 391 mahatan x10
# 392 mahatan x5
# 369 + levei


In [ ]:
def get_score_relevance(claim, cand):

    line_0 = underthesea.word_tokenize(claim, format="text")
    s0_tokenized = tokenizer_phobert_v2.encode(line_0, add_special_tokens=True)

    line_1 = underthesea.word_tokenize(cand, format="text")
    s1_tokenized = tokenizer_phobert_v2.encode(line_1, add_special_tokens=True)

    v_tokenized = s0_tokenized + s1_tokenized[1:]

    max_len = 250
    # Chèn thêm số 1 vào cuối câu nếu như không đủ 100 từ
    padded = numpy.array([v_tokenized + [1] * (max_len - len(v_tokenized))])

    attention_mask = numpy.where(padded == 1, 0, 1)

    padded = torch.tensor(padded).to(torch.long)
    attention_mask = torch.tensor(attention_mask)


    padded = padded.to(device)
    attention_mask = attention_mask.to(device)

    ranking_model.eval()
    # Lấy features dầu ra từ BERT
    with torch.no_grad():
        score = ranking_model(input_ids= padded, attention_mask=attention_mask)

    return score


progress = 0
def softmax_tensor(tensor_list):
    # Chuyển đổi danh sách tensor thành một tensor 1D
    tensor_1d = torch.cat([t.view(-1) for t in tensor_list])

    # Tính softmax
    softmax_values = torch.softmax(tensor_1d, dim=0)

    return softmax_values

def swaptop(top1, top2, diff_embedding, sorted_dict, threshold =0.5 ):
    # Lấy danh sách các key dựa trên giá trị giảm dần
    keys = list(sorted_dict.keys())

    # Kiểm tra xem giá trị top 1 có lớn hơn giá trị top 2 với một ngưỡng không
    if sorted_dict[top1] - sorted_dict[top2] <= threshold:
        # Nếu có, sử dụng hàm f để xử lý key top 1 và top 2
        if diff_embedding[top2] > diff_embedding[top1]:
            # Nếu hàm f trả về True, hoán đổi vị trí của key top 1 và top 2
            keys[0], keys[1] = keys[1], keys[0]

    # Tạo một dict mới với thứ tự key đã được cập nhật
    output_dict = {key: sorted_dict[key] for key in keys}

    return output_dict


def FindEvidence_V2(x, thres_value=None, top=5):
  global progress
  progress += 1
  print('#', progress)
  ids = [1]
  sorted_ctx_sents = []
  sorted_ctx_scores = []
  idxs = []
  # print(x)

  # ids.append(x.index[0])
  # chọn ra top các đoạn liên quan nhất trong x
  sents_of_ctx = split_context(str(x.context))
  tokenized_corpus = [doc.split(" ") for doc in sents_of_ctx]
  # Thay đổi hàm đo BM25 score ở đây
  bm25 = BM25Okapi(tokenized_corpus)
  query = str(x['claim'])
  tokenized_query = query.split(" ")
  doc_scores = bm25.get_scores(tokenized_query)
  sorted_ids = np.argsort(doc_scores, kind='mergesort')[::-1][:5]
  # print(str(x.evidence))
  value = 0.0
  if thres_value is not None:
      sorted_ctx_sents.append(np.array(sents_of_ctx)[sorted_ids[:thres_value]])
      sorted_ctx_scores.append(doc_scores[sorted_ids[:thres_value]])
      idxs.append(sorted_ids[:thres_value])
  elif thres_value is None:
      # thres_value = len(df)
      sorted_ctx_sents.append(np.array(sents_of_ctx)[sorted_ids])
      sorted_ctx_scores.append(doc_scores[sorted_ids])
      idxs.append(sorted_ids)


  QueryFeature = get_sentence_embedding(query)

  candidates = np.array(sents_of_ctx)[sorted_ids]
  # print(candidates)
  top = {}
  score = {}
  diff_embedding = {}

  for idx, candidate in enumerate(candidates):
    q = preprocess(query)
    c = preprocess(str(candidate))
    CandidateFeature = get_sentence_embedding(str(candidate))
    # embedding[str(candidate)] = CandidateFeature

    diff_embedding[str(candidate)] = calculate_cosine_similarity(QueryFeature, CandidateFeature)
    top[str(candidate)] = diff_embedding[str(candidate)]\
    + 0.07*sorted_ctx_scores[0][idx] \
    + 5*jaccard_similarity(q, c) \
    - 0.1*euclidean_distance(QueryFeature, CandidateFeature)\
    + 1*sentence_distance(q, c)

    score[str(candidate)] = get_score_relevance(q, c).cpu()

  # print(list(score.values()))
  softmax_values = softmax_tensor(list(score.values()))

  score = {key: value for key, value in zip(score.keys(), softmax_values)}

  top_dict = {key: top[key] + 4*score[key] for key in top}

  # print("TOP First", top)
  # print("TOP First", score)

  # print("TOP SCORE:", top_dict)





  sorted_dict = {k: v for k, v in sorted(top_dict.items(), key=lambda item: item[1], reverse=True)}
  # print("TOP SCORE:", sorted_dict)
  sorted_dict = swaptop(list(sorted_dict)[0], list(sorted_dict)[1], diff_embedding, sorted_dict)

  # print(sorted_dict)
  # print('___________________________________________________________________________________')


  return list(ids), list(sorted_ctx_sents), list(sorted_ctx_scores), list(idxs), sorted_dict

In [ ]:
_, _, _, _, d = FindEvidence_V2(df.loc[14453])

# 1


In [ ]:
d

{'Học phí đối với sinh viên quốc tế của trường dao động khoảng 50-100 triệu đồng một năm': tensor(7.0159, device='cuda:0'),
 'Học phí của Universidad Técnica Tederico Santa María (USM), Chile, trường đồng xếp hạng 386 với Đại học Quốc gia Hà Nội về ngành Kỹ thuật và Công nghệ, lên đến 4,5 tỷ đồng một năm': tensor(7.2809, device='cuda:0'),
 'Nếu không theo diện học bổng, sinh viên quốc tế đến Bách khoa đóng học phí bằng 1,5 lần so với học phí của sinh viên Việt Nam, mức "tương đối dễ chịu so" với các nước': tensor(2.9711, device='cuda:0'),
 'Với Choi, nếu học ở Hàn Quốc cao, mỗi năm nam sinh này tốn khoảng 100 triệu đồng học phí, trong khi học phí ở Việt Nam bằng một nửa, 50,5 triệu đồng': tensor(2.4764, device='cuda:0'),
 'Theo PGS.TS Nguyễn Phong Điền, sinh viên quốc tế đến Bách khoa du học làm tăng thêm tầm ảnh hưởng và thương hiệu của trường trong bối cảnh hội nhập quốc tế': tensor(2.2214, device='cuda:0')}

## ScoreEvidence

In [ ]:
# df_2 = pd.concat([df.loc[df['verdict']!='NEI'][:5000], df.loc[df['verdict']!='NEI'][-5000:]])

In [ ]:
# def ScoreEvidencePredict(df):
#   score_true = 0
#   for i in range(len(df)):
#     _,_,_,_,a = FindEvidence(df.iloc[i])
#     if preprocess(list(a)[0]) == preprocess(df.iloc[i].evidence):
#       score_true += 1
#     print("CURRENT SCORE", score_true)
#   print("FINALLY SCORE: ",score_true)
#   return score_true

In [ ]:
# print(ScoreEvidencePredict(df_2))

In [ ]:
def PrintErrorEvidencePredict(df):
  score_true = 0
  total = 0
  for i in range(len(df)):
    total += 1
    _,_,_,_,a = FindEvidence(df.iloc[i])
    if preprocess(list(a)[0]) != preprocess(df.iloc[i].evidence):
      score_true += 1
      print("CLAIM: ", df.iloc[i].claim)
      print("EVIDE: ", df.iloc[i].evidence)
      print("INDEX: ", df.iloc[i].index)
      print("PREDI: ", a)
      print('___________________________________________________________________________________')

    print("CURRENT ERROR", score_true/total)
  print("FINALLY ERROR: ",score_true/total)
  return score_true

In [ ]:
PrintErrorEvidencePredict(df[:1000])

# 244
CURRENT ERROR 0
# 245
CLAIM:  Thành lập năm 2016, phát triển phần mềm, tổ chức những dự án đào tạo kỹ năng nghề nghiệp, kỹ năng mềm, chú trọng xây dựng văn hoá doanh nghiệp là những dịch vụ FABA Technology chuyên cung cấp cho khách hàng.
EVIDE:  FABA Technology thành lập năm 2016, chuyên cung cấp dịch vụ phát triển phần mềm offshore cho nhiều khách hàng lớn trên toàn cầu như Mỹ, Australia, Singapore, và châu Âu
INDEX:  Index(['context', 'claim', 'verdict', 'evidence', 'domain'], dtype='object')
PREDI:  {'Bên cạnh đó, FABA thường xuyên tổ chức những dự án đào tạo kỹ năng nghề nghiệp, kỹ năng mềm, chú trọng xây dựng văn hoá doanh nghiệp để thúc đẩy phát triển đội ngũ': tensor(5.7907, device='cuda:0'), 'FABA Technology thành lập năm 2016, chuyên cung cấp dịch vụ phát triển phần mềm offshore cho nhiều khách hàng lớn trên toàn cầu như Mỹ, Australia, Singapore, và châu Âu': tensor(3.5960, device='cuda:0'), 'Phát biểu tại lễ ký kết vào ngày 17/11, Giám đốc điều hành kiêm đồng sáng lập F

183

In [ ]:
# 189 : 5*jaccard+0.1*bm25
# 207 : 5*jaccard
# 206 : 0.1*bm25
# 194 : 5*jaccard+0.3*bm25
# 187 : 5*jaccard+0.05*bm25
# 183 : 5*jaccard+0.05*bm25-0.1*euclide

In [ ]:
# remove_row = []

In [ ]:
#  a = list(df2[df2['evidence'].astype(str).apply(preprocess) != df2.apply(lambda row: process_func(row['claim'], row['context'], row['evidence']), axis=1)].index)

In [ ]:
# remove_row += a

In [ ]:
# df2.drop(remove_row, inplace=True)

In [ ]:
# df[(df['evidence'].astype(str).apply(preprocess) == df['claim'].astype(str).apply(preprocess)) & (df['verdict'] != "SUPPORTED")]


In [ ]:
# def process_func(claim, context, evidence):
#     # Thực hiện các thao tác xử lý trên 'claim' và 'context' tại đây
#     # Ví dụ: concatenate 'claim' và 'context'
#     sent= split_context(context)
#     for i in sent:
#       temp = preprocess(str(claim))
#       if preprocess(i) == temp:
#         return temp

#     return preprocess(str(evidence))

# # Áp dụng hàm 'process_func' lên cột 'claim' và 'context'
# # df3['processed_claim'] = df2.apply(lambda row: process_func(row['claim'], row['context']), axis=1)

# # In ra những hàng có 'evidence' khác với 'processed_claim'
# ad = df2_AGAIN[df2_AGAIN['evidence'].astype(str).apply(preprocess) != df2_AGAIN.apply(lambda row: process_func(row['claim'], row['context'], row['evidence']), axis=1)]

In [ ]:
# PRO = ad.index

In [ ]:
# df2_AGAIN.loc[PRO, 'verdict'] = 'SUPPORTED'
# df2_AGAIN.loc[PRO, 'evidence'] = df.loc[PRO, 'claim']


In [ ]:
# df2_AGAIN[(df2_AGAIN['evidence'].astype(str).apply(preprocess) != df2_AGAIN.apply(lambda row: process_func(row['claim'], row['context'], row['evidence']), axis=1)) & (df2_AGAIN['verdict']!="SUPPORTED")]

In [ ]:
# df2_AGAIN = pd.concat([df2, df3.loc[list(ad)]])

In [ ]:
# df2_AGAIN.to_json('/content/drive/MyDrive/Colab Notebooks/DS/data/ise-dsc01-train_BEST.json', orient='index', force_ascii=False)
#

In [ ]:
# file_path3 = "/content/drive/MyDrive/Colab Notebooks/DS/data/ise-dsc01-train_BEST.json"
# df3 = pd.read_json(file_path3, orient='index')

In [ ]:
# df4 = pd.read_json(file_path3, orient='index')

In [ ]:
# _,_,_,_,a = FindEvidence(df.loc[7323])
# print("E: ", df.loc[7323].evidence)
# print("P: ",list(a)[0])
# if preprocess(list(a)[0]) != preprocess(df.loc[7323].evidence):

#   print("ERROR")

In [ ]:
# 550 2
# 671 1
# 762 1+jaccard
# 624 -manhatan
# 646 -0.1manhatan
# 744 -0.01manhatan

In [ ]:
# Sau khi thay đổi phương pháp, dành nhiều thời gian học tập hơn, Tâm đã vươn lên và lọt vào top 10 của lớp.
# EVIDE:  Từ một học sinh ở nhóm giữa, em vươn lên, lọt vào top 10 của lớp.
# PREDI:  {'Nhưng sau đó, em thay đổi phương pháp và dành nhiều thời gian hơn cho việc học': 2.846864305693528, 'Từ một học sinh ở nhóm giữa, em vươn lên, lọt vào top 10 của lớp': 2.236809326756385,

In [ ]:
# sentence1 = "Sau khi thay đổi phương pháp, dành nhiều thời gian học tập hơn, Tâm đã vươn lên và lọt vào top 10 của lớp"
# sentence1_1 = "Tâm đã vươn lên và lọt vào top 10 của lớp"
# sentence1_2 = "dành nhiều thời gian học tập hơn"
# sentence1_3 = "Sau khi thay đổi phương pháp"
# sentence2 = "Nhưng sau đó, em thay đổi phương pháp và dành nhiều thời gian hơn cho việc học"
# sentence3 = "Từ một học sinh ở nhóm giữa, em vươn lên, lọt vào top 10 của lớp"
# sentence4 =  'lọt vào top 10 của lớp'


# Tính toán và in ra độ tương đồng cosine
# print(euclidean_distance(sentence1, sentence2))
# print(euclidean_distance(sentence1, sentence3))

In [ ]:
# s1 = get_sentence_embedding(sentence1)
# s2 = get_sentence_embedding(sentence2)
# s3 = get_sentence_embedding(sentence3)
# s4 = get_sentence_embedding(sentence4)
# s1_1 = get_sentence_embedding(sentence1_1)
# s1_2 = get_sentence_embedding(sentence1_2)
# s1_3 = get_sentence_embedding(sentence1_3)

In [ ]:
# print(calculate_cosine_similarity(s1, s2) + 5*jaccard_similarity(sentence1, sentence2))
# print(calculate_cosine_similarity(s1, s3) + 5*jaccard_similarity(sentence1, sentence3))
# print(calculate_cosine_similarity(s1, s4) + 5*jaccard_similarity(sentence1, sentence4))


In [ ]:
# print(calculate_cosine_similarity(s1_1, s2) + 5*jaccard_similarity(sentence1_1, sentence2))
# print(calculate_cosine_similarity(s1_1, s3) + 5*jaccard_similarity(sentence1_1, sentence3))
# print(calculate_cosine_similarity(s1_1, s4) + 5*jaccard_similarity(sentence1_1, sentence4))

In [ ]:
# print(calculate_cosine_similarity(s1_2, s2) + 5*jaccard_similarity(sentence1_2, sentence2))
# print(calculate_cosine_similarity(s1_2, s3) + 5*jaccard_similarity(sentence1_2, sentence3))
# print(calculate_cosine_similarity(s1_2, s4) + 5*jaccard_similarity(sentence1_2, sentence4))

In [ ]:
# print(calculate_cosine_similarity(s1_3, s2) + 5*jaccard_similarity(sentence1_3, sentence2))
# print(calculate_cosine_similarity(s1_3, s3) + 5*jaccard_similarity(sentence1_3, sentence3))
# print(calculate_cosine_similarity(s1_3, s4) + 5*jaccard_similarity(sentence1_3, sentence4))

In [ ]:
# print(calculate_cosine_similarity(s1, s2) )
# print(calculate_cosine_similarity(s1, s3) )
# print(calculate_cosine_similarity(s1, s4) )

In [ ]:
# print(jaccard_similarity(sentence1, sentence2))
# print( jaccard_similarity(sentence1, sentence3))
# print( jaccard_similarity(sentence1, sentence4))

In [ ]:
# from gensim.models import KeyedVectors
# from sklearn.metrics.pairwise import cosine_similarity

# # Load Word2Vec model (you might need to download it first)
# model = KeyedVectors.load_word2vec_format('GoogleNews-vectors-negative300.bin', binary=True)

# def jaccard_similarity(sentence1, sentence2):
#     words1 = set(sentence1.split())
#     words2 = set(sentence2.split())

#     intersection = set()
#     for word1 in words1:
#         for word2 in words2:
#             if word1 in model and word2 in model and cosine_similarity([model[word1]], [model[word2]])[0][0] > 0.5:
#                 intersection.add(word1)
#                 break

#     union = words1.union(words2)

#     return len(intersection) / len(union)

# # Example usage:
# sentence1 = 'I feel happy'
# sentence2 = 'I am glad'
# print(jaccard_similarity(sentence1, sentence2))


In [ ]:
# pip install https://gitlab.com/trungtv/vi_spacy/-/raw/master/packages/vi_core_news_lg-3.6.0/dist/vi_core_news_lg-3.6.0.tar.gz


In [ ]:
# pip install pyvi

In [ ]:
# from spacy.lang.vi import Vietnamese
# nlp = Vietnamese()
# doc = nlp('Bách Khoa Hà Nội')


In [ ]:
# import spacy
# nlp = spacy.load('vi_core_news_lg')

In [ ]:
# doc = nlp('Chị Uyên đã được một học viên nam bị khuyết tật bẩm sinh truyền tải nhiều năng lượng tích cực')
# for token in doc:
#     print(token.text, token.lemma_, token.pos_, token.tag_, token.dep_,
#             token.shape_, token.is_alpha, token.is_stop)

In [ ]:
# for token in doc:
#     if token.dep_ == 'nsubj':
#         print(f"Chủ ngữ: {token.text}")
#     if token.dep_ == 'ROOT' or any(child.dep_ == 'relcl' for child in token.children):
#         print(f"Vị ngữ: {token.text}")

# # Ý chính của câu
# print(f"Ý chính: {doc.ents}")

## Split


In [ ]:
X = df[['claim', 'evidence','verdict', 'context']]
y = df['verdict']

In [ ]:
# X_train.loc[X_train['verdict'] == 'NEI']

In [ ]:
# X_train.loc[663:1882, 'evidence'] = X_train.loc[663:1882].apply(lambda row: list(FindEvidence(row, top=1)[4].keys())[0], axis=1)

In [ ]:
# X_train = X_train.loc[X_train['verdict'] == 'NEI'][-10:]

## Update 'evidence' -> 'NEI'

In [ ]:
# X_train.loc[X_train['evidence'].isnull(), 'evidence']

In [ ]:
X.loc[X['evidence'].isnull(), 'evidence'] = X.loc[X['verdict'] == 'NEI'].apply(lambda row: list(FindEvidence_V2(row, top=1)[4].keys())[0], axis=1)

Streaming output truncated to the last 5000 lines.
# 7
# 8
# 9
# 10
# 11
# 12
# 13
# 14
# 15
# 16
# 17
# 18
# 19
# 20
# 21
# 22
# 23
# 24
# 25
# 26
# 27
# 28
# 29
# 30
# 31
# 32
# 33
# 34
# 35
# 36
# 37
# 38
# 39
# 40
# 41
# 42
# 43
# 44
# 45
# 46
# 47
# 48
# 49
# 50
# 51
# 52
# 53
# 54
# 55
# 56
# 57
# 58
# 59
# 60
# 61
# 62
# 63
# 64
# 65
# 66
# 67
# 68
# 69
# 70
# 71
# 72
# 73
# 74
# 75
# 76
# 77
# 78
# 79
# 80
# 81
# 82
# 83
# 84
# 85
# 86
# 87
# 88
# 89
# 90
# 91
# 92
# 93
# 94
# 95
# 96
# 97
# 98
# 99
# 100
# 101
# 102
# 103
# 104
# 105
# 106
# 107
# 108
# 109
# 110
# 111
# 112
# 113
# 114
# 115
# 116
# 117
# 118
# 119
# 120
# 121
# 122
# 123
# 124
# 125
# 126
# 127
# 128
# 129
# 130
# 131
# 132
# 133
# 134
# 135
# 136
# 137
# 138
# 139
# 140
# 141
# 142
# 143
# 144
# 145
# 146
# 147
# 148
# 149
# 150
# 151
# 152
# 153
# 154
# 155
# 156
# 157
# 158
# 159
# 160
# 161
# 162
# 163
# 164
# 165
# 166
# 167
# 168
# 169
# 170
# 171
# 172
# 173
# 174
# 175
# 176
# 177
# 178
# 179
# 180
#

KeyboardInterrupt: ignored

In [ ]:
X.to_json('/content/drive/MyDrive/Colab Notebooks/DS/data/X_filled_V3.json', orient='index', force_ascii=False)


# Prepare data for Model

In [ ]:
X = pd.read_json("/content/drive/MyDrive/Colab Notebooks/DS/data/X_filled_V3.json", orient='index')

In [ ]:
from sklearn.model_selection import train_test_split

y = X['verdict']
# Train Test Split
X_train, X_val, y_train, y_val = train_test_split(
    X, y, test_size=0.1, random_state=42)

# Data Loader

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from transformers import AdamW
from tqdm import tqdm
from sklearn.preprocessing import LabelEncoder

In [ ]:
from torch.utils.data import Dataset, DataLoader

In [ ]:
def CreatePairPOS_NEG(data):
    POS_LIST = []
    NEG_LIST = []
    mask_POS = []
    mask_NEG = []

    for idx in range(len(data)):
        claim = data.iloc[idx]['claim']
        evidence = data.iloc[idx]['evidence']
        evi_pre = preprocess(evidence)

        _, _, _, _, top = FindEvidence(data.iloc[idx])

        NEG_DOC = []

        for i in range(len(top)):
          cand = preprocess(list(top)[i])
          if cand != evi_pre:
            NEG_DOC.append(cand)


        s0 = preprocess(claim)
        line_0 = underthesea.word_tokenize(s0, format="text")
        s0_tokenized = tokenizer_phobert_v2.encode(line_0, add_special_tokens=True)

        line_1 = underthesea.word_tokenize(evi_pre, format="text")
        s1_tokenized = tokenizer_phobert_v2.encode(line_1, add_special_tokens=True)

        POS_token = s0_tokenized + s1_tokenized[1:]


        # Chèn thêm số 1 vào cuối câu nếu như không đủ 200 từ
        POS_token = numpy.array([POS_token + [1] * (250 - len(POS_token))])
        attention_mask_POS = numpy.where(POS_token == 1, 0, 1)

        for cand in NEG_DOC:
            line_2 = underthesea.word_tokenize(cand, format="text")
            s2_tokenized = tokenizer_phobert_v2.encode(line_2, add_special_tokens=True)

            NEG_token = s0_tokenized + s2_tokenized[1:]
            if len(NEG_token) < 250:
                NEG_token = NEG_token + [1] * (250 - len(NEG_token))
            elif len(NEG_token) > 250:
                NEG_token = NEG_token[:250]

            # Chuyển NEG_token thành một mảng numpy
            NEG_token = numpy.array([NEG_token])

            # Tạo attention_mask_NEG dựa trên NEG_token
            attention_mask_NEG = numpy.where(NEG_token == 1, 0, 1)

            POS_LIST.append(POS_token)
            NEG_LIST.append(NEG_token)
            mask_POS.append(attention_mask_POS)
            mask_NEG.append(attention_mask_NEG)

    print(len(POS_LIST))
          # print(np.shape(POS_token))
    return {
        'POS': POS_LIST,
        'NEG': NEG_LIST,
        'mask_pos': mask_POS,
        'mask_neg': mask_NEG
    }

In [ ]:
class EvidenceDataset(Dataset):
    def __init__(self, data):
        self.data = data

    def __len__(self):
        return len(self.data['POS'])

    def __getitem__(self, idx):
        POS_token = self.data['POS'][idx]
        NEG_token = self.data['NEG'][idx]
        mask_pos = self.data['mask_pos'][idx]
        mask_neg = self.data['mask_neg'][idx]
        return {
            'POS': POS_token,
            'NEG': NEG_token,
            'mask_pos': mask_pos,
            'mask_neg': mask_neg
        }

In [ ]:
# Định nghĩa class Dataset
class TextDataset(Dataset):
    def __init__(self, sentence_pairs, labels):
        self.sentence_pairs = sentence_pairs
        self.labels = labels
        self.max_len = 250

    def __len__(self):
        return len(self.sentence_pairs)

    def __getitem__(self, idx):
        claim, evidence = self.sentence_pairs[idx]
        label = self.labels[idx]

        s1 = preprocess(claim)
        s2 = preprocess(evidence)

        line_1 = underthesea.word_tokenize(s1, format="text")
        line_2 = underthesea.word_tokenize(s2, format="text")

        # Tokenize câutokenizer_phobert_v2.encode(line)
        s1_tokenized = tokenizer_phobert_v2.encode(line_1, add_special_tokens=True)
        s2_tokenized = tokenizer_phobert_v2.encode(line_2, add_special_tokens=True)[1:]

        v_tokenized = s1_tokenized + s2_tokenized

        # Chèn thêm số 1 vào cuối câu nếu như không đủ 200 từ
        padded = numpy.array([v_tokenized + [1] * (self.max_len - len(v_tokenized))])
        attention_mask = numpy.where(padded == 1, 0, 1)

        padded = torch.tensor(padded).to(torch.long)
        attention_mask = torch.tensor(attention_mask)

        padded = padded.to(device)
        attention_mask = attention_mask.to(device)

        with torch.no_grad():
          outputs = phobert_v2(input_ids = padded, attention_mask = attention_mask)

        v_features = outputs[2]

        return {
            'outputs': v_features,
            # 'mask': torch.tensor(attention_mask, dtype=torch.long),
            'targets': torch.tensor(label, dtype=torch.float)
        }

In [ ]:
labels = ['SUPPORTED', 'REFUTED', 'NEI']

encoder = LabelEncoder()
encoder.fit(labels)

LabelEncoder()

# Model Classifier

## Classifier Train function

In [ ]:
def train(model, train_loader, val_loader, path, epochs = 10, learning_rate = 1e-5, loss_fn = torch.nn.CrossEntropyLoss()):
  optimizer = AdamW(model.parameters(), lr=learning_rate, correct_bias=True, weight_decay=1e-3)

  len_data_train = len(train_dataset)
  len_train_loader = len(train_loader)
  len_val_input_data = len(X_val_input_data)

  LOSS_HIS = []
  TRAIN_ACC_HIS = []
  VAL_ACC_HIS = []

  best_accuracy = 0.0
  # Huấn luyện mô hình
  for epoch in range(epochs):  # Số epoch có thể thay đổi tùy theo nhu cầu của bạn
      model.train()
      correct_predictions_train = 0
      total_loss=0

      for batch in tqdm(train_loader):

          input = batch['outputs']
          # mask = batch['mask'].to(device)
          targets = batch['targets'].to(device)

          outputs = model(input)

          targets = targets.long()

          optimizer.zero_grad()
          loss = loss_fn(outputs, targets)
          total_loss += loss.item()  # Tính tổng loss

          preds_train = outputs.argmax(dim=1)

  # Tính số lượng dự đoán chính xác
          correct = (preds_train == targets).sum().item()
          correct_predictions_train += correct

          loss.backward()
          optimizer.step()

          print(' - Train Accuracy - Batch: {}%'.format(100 * correct / targets.size(0)))
          print(' - Loss - Batch: {}'.format(loss.item()))
      print(f'Epoch: {epoch+1}, Loss: {total_loss}')
      LOSS_HIS.append(total_loss)


      train_acc = 100 * correct_predictions_train / len_data_train  # Tính độ chính xác trên tập huấn luyện
      avg_loss = total_loss / len_train_loader  # Tính giá trị trung bình của loss
      print(f'Training Accuracy - Total : {train_acc:.4f}')
      print(f'Average loss - Batch: {avg_loss:.4f}')
      TRAIN_ACC_HIS.append(train_acc)

      # Đánh giá mô hình trên tập validation sau mỗi epoch
      model.eval()
      correct_predictions_val = 0
      with torch.no_grad():
          for batch in tqdm(val_loader):
              input = batch['outputs']
              # mask = batch['mask'].to(device)
              targets = batch['targets'].to(device)

              outputs = model(input)
              preds_val = outputs.argmax(dim=1)
              correct_predictions_val += (preds_val == targets).sum().item()

      val_acc = 100 * correct_predictions_val / len_val_input_data
      print('Validation Accuracy: {}%'.format(val_acc))
      print('___________________________________________________________')
      VAL_ACC_HIS.append(val_acc)

      if val_acc >= best_accuracy:
        best_accuracy = val_acc
        torch.save({
            'epoch': epoch,
            'model_state_dict': model.state_dict(),
            'optimizer_state_dict': optimizer.state_dict(),
            'accuracy': val_acc,
            }, path)

  return LOSS_HIS, TRAIN_ACC_HIS, VAL_ACC_HIS

## Ranking Learning Train function


In [ ]:
def ranking_learning(model, train_loader, val_loader, path, epochs = 10, learning_rate = 3e-5, loss_fn = torch.nn.CrossEntropyLoss()):
  optimizer = AdamW(model.parameters(), lr=learning_rate, correct_bias=False, weight_decay=1e-4)

  len_data_train = len(dataPairTrainMIDDLE['POS'])
  len_train_loader = len(train_loader)
  len_val_input_data = len(dataPairVal['POS'])

  LOSS_HIS = []
  TRAIN_ACC_HIS = []
  VAL_ACC_HIS = []

  best_accuracy = 0.0
  # Huấn luyện mô hình
  for epoch in range(epochs):  # Số epoch có thể thay đổi tùy theo nhu cầu của bạn
      model.train()
      correct_predictions_train = 0
      total_loss=0

      for batch in tqdm(train_loader):
          correct = 0

          POS_DOC = batch['POS']
          # print("POS_DOC, ", np.shape(POS_DOC))
          attention_mask_POS = batch['mask_pos']
          POS = POS_DOC.to(device).to(torch.long).squeeze(1)
          attention_mask_POS = attention_mask_POS.to(device).squeeze(1)

          NEG_DOC = batch['NEG']
          attention_mask_NEG = batch['mask_neg']
          NEG = NEG_DOC.to(torch.long).to(device).squeeze(1)
          attention_mask_NEG = attention_mask_NEG.to(device).squeeze(1)



          pos_output = model(input_ids = POS, attention_mask = attention_mask_POS)
          neg_output = model(input_ids = NEG, attention_mask = attention_mask_NEG)

          output = torch.stack((pos_output, neg_output), dim=1)

          targets = torch.zeros(len(POS_DOC), dtype=torch.long).to(device)

          optimizer.zero_grad()

          output = output.squeeze(2)

          loss = loss_fn(output, targets)
          total_loss += loss.item()

          preds_train = torch.argmax(output, dim=1)
          correct += (preds_train == targets).sum().item()

          loss.backward()
          optimizer.step()

          correct_predictions_train += correct
          print(' - Train Accuracy - Batch: {}%'.format(100 * correct / targets.size(0)))
          print(' - Loss - Batch: {}'.format(loss.item()))
      print(f'Epoch: {epoch+1}, Loss: {total_loss}')
      LOSS_HIS.append(total_loss)

      train_acc = 100 * correct_predictions_train / len_data_train  # Tính độ chính xác trên tập huấn luyện
      avg_loss = total_loss / len_train_loader  # Tính giá trị trung bình của loss
      print(f'Training Accuracy - Total : {train_acc:.4f}')
      print(f'Average loss - Batch: {avg_loss:.4f}')
      TRAIN_ACC_HIS.append(train_acc)


      # Đánh giá mô hình trên tập validation sau mỗi epoch
      model.eval()
      correct_predictions_val = 0
      with torch.no_grad():
          for batch in tqdm(val_loader):

              POS_DOC = batch['POS']
              attention_mask_POS = batch['mask_pos']
              POS = POS_DOC.to(device).to(torch.long).squeeze(1)
              attention_mask_POS = attention_mask_POS.to(device).squeeze(1)

              NEG_DOC = batch['NEG']
              attention_mask_NEG = batch['mask_neg']
              NEG = NEG_DOC.to(torch.long).to(device).squeeze(1)
              attention_mask_NEG = attention_mask_NEG.to(device).squeeze(1)

              pos_output = model(input_ids = POS, attention_mask = attention_mask_POS)
              neg_output = model(input_ids = NEG, attention_mask = attention_mask_NEG)

              output = torch.stack((pos_output, neg_output), dim=1)
              labels = torch.zeros(len(POS_DOC), dtype=torch.long).to(device)

              preds_val = torch.argmax(output, dim=1).squeeze()
              correct_predictions_val += (preds_val == labels).sum().item()


      val_acc = 100 * correct_predictions_val / len_val_input_data
      print('Validation Accuracy: {}%'.format(val_acc))
      print('___________________________________________________________')
      VAL_ACC_HIS.append(val_acc)

      if val_acc >= best_accuracy:
          best_accuracy = val_acc
          torch.save({
              'epoch': epoch,
              'model_state_dict': model.state_dict(),
              'optimizer_state_dict': optimizer.state_dict(),
              'accuracy': val_acc,
              }, path)

  return LOSS_HIS, TRAIN_ACC_HIS, VAL_ACC_HIS

## RankingModel


In [ ]:
class RankingModel(nn.Module):
    def __init__(self, bert_model, num_classes):
        super(RankingModel, self).__init__()
        self.bert = bert_model
        self.fc = nn.Linear(768, num_classes)

    def forward(self, input_ids, attention_mask):
        bert_output = self.bert(input_ids=input_ids, attention_mask=attention_mask)[0]
        bert_output = bert_output[:, 0, :]
        output = self.fc(bert_output)
        return output

In [ ]:
phobert_v2_ranking = AutoModel.from_pretrained("vinai/phobert-base-v2", output_hidden_states=True)
phobert_v2_ranking = phobert_v2_ranking.to(device)

# Khởi tạo mô hình
ranking_model = RankingModel(phobert_v2_ranking, num_classes=1).to(device)

Some weights of RobertaModel were not initialized from the model checkpoint at vinai/phobert-base-v2 and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
checkpoint = torch.load('/content/drive/MyDrive/Colab Notebooks/DS/best_model_RANKING.pth')
ranking_model.load_state_dict(checkpoint['model_state_dict'])

<All keys matched successfully>

## MLP

In [ ]:
# Định nghĩa mô hình Neural Network
class MLP(torch.nn.Module):
    def __init__(self):
        super(MLP, self).__init__()
        self.layers = nn.Sequential(
            nn.Linear(768*4, 512),
            nn.ReLU(),
            nn.Dropout(0.5),
            nn.Linear(512, 3)
        )
        self.bn = nn.BatchNorm1d(768*4)

    def forward(self, outputs):
        # print("DDDDD: ", outputs[-1][:, 0, ...][:, 0, ...].size())
        output = torch.cat((outputs[-1][:, 0, ...][:, 0, ...],outputs[-2][:, 0, ...][:, 0, ...], outputs[-3][:, 0, ...][:, 0, ...], outputs[-4][:, 0, ...][:, 0, ...]),-1)
        output = output.to(device)
        # print("OOOOO: ", output.size())
        # Thay đổi kích thước của tensor
        output = self.bn(output)
        out = self.layers(output)
        # print("EEEEE: ", out.size())

        return out

In [ ]:
# Khởi tạo mô hình và chuyển lên GPU
model_0 = MLP()
model_0 = model_0.to(device)

## Conv

In [ ]:
import torch.nn as nn
import torch.nn.functional as F

class CNN(nn.Module):
    def __init__(self):
        super(CNN, self).__init__()
        self.conv1 = nn.Conv1d(3072, 512, kernel_size=5, stride=1, padding=1)
        # self.bn1 = nn.BatchNorm1d(512)
        self.dropout1 = nn.Dropout(0.65)
        self.pool = nn.MaxPool1d(kernel_size=2, stride=2)

        self.conv2 = nn.Conv1d(512, 256, kernel_size=3, stride=1, padding=1)
        self.bn2 = nn.BatchNorm1d(256)
        # self.dropout2 = nn.Dropout(0.3)

        self.fc1 = nn.Linear(15872, 512)
        self.fc2 = nn.Linear(512, 64)
        self.fc3 = nn.Linear(64, 3)

    def forward(self, outputs):
        # with torch.no_grad():
        #     outputs = phobert_v2(input_ids= ids, attention_mask=mask)
        # print(np.shape(outputs))
        output = torch.cat((outputs[-1],outputs[-2], outputs[-3], outputs[-4]),-1)
        output = output.to(device)
        # print("OUTPUT SIZE: ", output.size())
        # print("O SIZE: ",outputs[0].size())
        # x = output.unsqueeze(0)
        x = output.squeeze(1)
        x = x.permute(0, 2, 1)
        # print("INPUT SIZE: ",x.size())

        x = F.relu(self.conv1(x))
        # print("CON+BA: ", x.size())
        x = self.pool(x)
        # print("POOL 1: " , x.size())
        x = F.relu(self.conv2(x))
        x = self.pool(x)
        x = self.bn2(x)
        # print("POOL 2: " , x.size())

        x = x.view(x.size(0), -1)

        x = self.fc1(x)
        x = F.relu(x)
        x = self.dropout1(x)

        x = self.fc2(x)
        x = F.relu(x)
        x = self.dropout1(x)
        x = self.fc3(x)

        return x

In [ ]:
class CNN_2(nn.Module):
    def __init__(self):
        super(CNN_2, self).__init__()
        self.conv1 = nn.Conv1d(3072, 256, kernel_size=5, stride=1, padding=1)
        # self.bn1 = nn.BatchNorm1d(512)
        self.dropout1 = nn.Dropout(0.75)
        self.pool = nn.MaxPool1d(kernel_size=2, stride=2)

        self.bn2 = nn.BatchNorm1d(256)
        # self.dropout2 = nn.Dropout(0.3)

        self.fc1 = nn.Linear(31744, 3)


    def forward(self, outputs):
        # with torch.no_grad():
        #     outputs = phobert_v2(input_ids= ids, attention_mask=mask)
        # print(np.shape(outputs))
        output = torch.cat((outputs[-1],outputs[-2], outputs[-3], outputs[-4]),-1)
        output = output.to(device)
        # print("OUTPUT SIZE: ", output.size())
        # print("O SIZE: ",outputs[0].size())
        # x = output.unsqueeze(0)
        x = output.squeeze(1)
        x = x.permute(0, 2, 1)
        # print("INPUT SIZE: ",x.size())

        x = F.relu(self.conv1(x))
        # print("CON+BA: ", x.size())
        x = self.pool(x)
        # print("POOL 1: " , x.size())
        x = self.bn2(x)
        # print("POOL 2: " , x.size())

        x = x.view(x.size(0), -1)
        x = self.dropout1(x)
        x = self.fc1(x)


        return x

# Training


## Train Classifier

In [ ]:
X_train_input_data = X_train[['claim', 'evidence']].values.tolist()

encoded_labels = encoder.transform(y_train)
labels_tensor = torch.Tensor(encoded_labels)
labels_train = labels_tensor.long()

X_val_input_data = X_val[['claim', 'evidence']].values.tolist()

encoded_labels_val = encoder.transform(y_val)
labels_tensor = torch.Tensor(encoded_labels_val)
labels_val = labels_tensor.long()

# Khởi tạo Dataset cho tập huấn luyện và tập validation
train_dataset = TextDataset(X_train_input_data, labels_train)
val_dataset = TextDataset(X_val_input_data, labels_val)

# Khởi tạo DataLoader cho tập huấn luyện và tập validation
train_loader = DataLoader(train_dataset, batch_size=128, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=64)

In [ ]:
X.loc[X['verdict'] == "NEI"]

claim  \
297    Cạnh đó, thanh niên quân đội và thanh niên tiề...   
298    Gương mặt trẻ tiêu biểu, Gương mặt trẻ triển v...   
299    10 gương mặt trẻ tiêu biểu, 43 gương mặt triển...   
300    Nằm trên tỉnh Khánh Hòa, dự án Nha Trang - Cam...   
301    Hai dự án sẽ nâng tổng số km cao tốc trục Bắc ...   
...                                                  ...   
29202  Tỉ lệ tử vong do ung thư dạ dày hiện đang cao ...   
29203  Nam giới vẫn có khả năng có con một cách tự nh...   
29204  Nữ giới mang thai sau 35 tuổi làm con tăng khả...   
29205  Nam giới nên có chế độ ăn hợp lí để duy trì ch...   
29206   Suy sinh dục dưới đồi không mang tính di truyền.   

                                                evidence verdict  \
297    Cạnh đó, thanh niên quân đội cũng phải thực hi...     NEI   
298    Gương mặt trẻ tiêu biểu, Gương mặt trẻ triển v...     NEI   
299    10 gương mặt trẻ tiêu biểu, 43 gương mặt triển...     NEI   
300    Nằm trên tỉnh Khánh Hòa, dự án Nha Trang - Cam...     NEI   
301    Hai dự án sẽ nâng tổng số km cao tốc trục Bắc ...     NEI   
...                                                  ...     ...   
29202  Tuy nhiên, hiện bệnh có xu hướng trẻ hóa, tỷ l...     NEI   
29203  Nam giới có khả năng sản xuất tinh trùng và du...     NEI   
29204  Ở nữ giới, tuổi tác không chỉ gây khó khăn tro...     NEI   
29205  Nam giới có khả năng sản xuất tinh trùng và du...     NEI   
29206  Các xét nghiệm bổ sung bao gồm kiểm tra máu nh...     NEI   

                                                 context  
297    Thay mặt 10 thanh niên tiêu biểu nhận bằng khe...  
298    Thay mặt 10 thanh niên tiêu biểu nhận bằng khe...  
299    Thay mặt 10 thanh niên tiêu biểu nhận bằng khe...  
300    Lễ khánh thành dự án thành phần cao tốc Bắc Na...  
301    Lễ khánh thành dự án thành phần cao tốc Bắc Na...  
...                                                  ...  
29202  Bệnh về đường tiêu hóa rất phổ biến tại Việt N...  
29203  Bác sĩ Lê Duy Thảo, Khoa Nam học, Bệnh viện đa...  
29204  Bác sĩ Lê Duy Thảo, Khoa Nam học, Bệnh viện đa...  
29205  Bác sĩ Lê Duy Thảo, Khoa Nam học, Bệnh viện đa...  
29206  Ngày 3/8, các bác sĩ cho biết lông sinh dục bệ...  

[12436 rows x 4 columns]

In [ ]:
# Khởi tạo mô hình và chuyển lên GPU
model_2 = CNN_2()
model_2 = model_2.to(device)

In [ ]:
# Khởi tạo mô hình và chuyển lên GPU
model_1 = CNN()
model_1 = model_1.to(device)

In [ ]:
def count_parameters(model):
    return sum(p.numel() for p in model.parameters() if p.requires_grad)

# print(f'The model DNN has {count_parameters(model)} trainable parameters')

print(f'The model Conv has {count_parameters(model_2)} trainable parameters')

The model Conv has 3980547 trainable parameters


In [ ]:
LOSS_HIS, TRAIN_ACC_HIS, VAL_ACC_HIS = train(model_2, train_loader, val_loader, epochs = 5, learning_rate = 1e-4, path = '/content/drive/MyDrive/Colab Notebooks/DS/best_model_CNN_2.pth')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
  0%|          | 0/265 [00:00<?, ?it/s]<ipython-input-19-0220c28d08bb>:45: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'targets': torch.tensor(label, dtype=torch.float)
  0%|          | 1/265 [00:05<24:26,  5.55s/it]

 - Train Accuracy - Batch: 37.5%
 - Loss - Batch: 1.393807291984558


  1%|          | 2/265 [00:08<18:25,  4.20s/it]

 - Train Accuracy - Batch: 35.15625%
 - Loss - Batch: 1.4710572957992554


  1%|          | 3/265 [00:11<14:58,  3.43s/it]

...

 - Train Accuracy - Batch: 82.03125%
 - Loss - Batch: 0.5249058604240417


 18%|█▊        | 49/265 [02:01<09:11,  2.55s/it]

 - Train Accuracy - Batch: 82.03125%
 - Loss - Batch: 0.4379073977470398


 18%|█▊        | 49/265 [02:02<09:00,  2.50s/it]


KeyboardInterrupt: ignored

In [ ]:
LOSS_HIS, TRAIN_ACC_HIS, VAL_ACC_HIS = train(model_0, train_loader, val_loader, epochs = 5, learning_rate = 1e-4, path = '/content/drive/MyDrive/Colab Notebooks/DS/best_model_MLP_V1.pth')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
  0%|          | 0/133 [00:00<?, ?it/s]<ipython-input-20-0220c28d08bb>:45: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'targets': torch.tensor(label, dtype=torch.float)
  1%|          | 1/133 [00:05<11:09,  5.07s/it]

 - Train Accuracy - Batch: 31.25%
 - Loss - Batch: 1.1487820148468018


  2%|▏         | 2/133 [00:10<11:28,  5.26s/it]

 - Train Accuracy - Batch: 42.578125%
 - Loss - Batch: 1.088783860206604


  2%|▏         | 3/133 [00:15<11:19,  5.23s/it]

...

 - Train Accuracy - Batch: 77.34375%
 - Loss - Batch: 0.5559974908828735


100%|██████████| 133/133 [10:35<00:00,  4.78s/it]


 - Train Accuracy - Batch: 73.91304347826087%
 - Loss - Batch: 0.6501583456993103
Epoch: 5, Loss: 77.89509257674217
Training Accuracy - Total : 75.8792
Average loss - Batch: 0.5857


100%|██████████| 59/59 [01:10<00:00,  1.19s/it]

Validation Accuracy: 73.59042553191489%
___________________________________________________________


In [ ]:
LOSS_HIS, TRAIN_ACC_HIS, VAL_ACC_HIS = train(model_0, train_loader, val_loader, epochs = 5, learning_rate = 1e-3, path = '/content/drive/MyDrive/Colab Notebooks/DS/best_model_MLP_V1.pth')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
  0%|          | 0/133 [00:00<?, ?it/s]<ipython-input-20-0220c28d08bb>:45: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'targets': torch.tensor(label, dtype=torch.float)
  1%|          | 1/133 [00:04<09:16,  4.22s/it]

 - Train Accuracy - Batch: 77.734375%
 - Loss - Batch: 0.557007372379303


  2%|▏         | 2/133 [00:09<10:53,  4.98s/it]

 - Train Accuracy - Batch: 67.96875%
 - Loss - Batch: 0.7513784766197205


  2%|▏         | 3/133 [00:14<10:10,  4.70s/it]

...

 - Train Accuracy - Batch: 71.875%
 - Loss - Batch: 0.6282872557640076


 11%|█         | 14/133 [01:06<09:27,  4.77s/it]

 - Train Accuracy - Batch: 72.65625%
 - Loss - Batch: 0.6909809708595276


 11%|█         | 14/133 [01:07<09:30,  4.79s/it]


KeyboardInterrupt: ignored

In [ ]:
LOSS_HIS1, TRAIN_ACC_HIS1, VAL_ACC_HIS1 = train(model_1, train_loader, val_loader, epochs = 3, learning_rate = 5e-5, path = '/content/drive/MyDrive/Colab Notebooks/DS/best_model_V2.pth')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
  0%|          | 0/133 [00:00<?, ?it/s]<ipython-input-23-0220c28d08bb>:45: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'targets': torch.tensor(label, dtype=torch.float)


 - Train Accuracy - Batch: 95.3125%


  1%|          | 1/133 [00:05<11:35,  5.27s/it]

 - Loss - Batch: 0.15737122297286987
 - Train Accuracy - Batch: 94.53125%


  2%|▏         | 2/133 [00:10<11:49,  5.41s/it]

...

 - Loss - Batch: 0.024306155741214752


100%|██████████| 133/133 [11:23<00:00,  5.14s/it]


 - Train Accuracy - Batch: 100.0%
 - Loss - Batch: 0.008334780111908913
Epoch: 3, Loss: 3.8338441578671336
Training Accuracy - Total : 99.3646
Average loss - Batch: 0.0288


100%|██████████| 59/59 [01:12<00:00,  1.22s/it]

Validation Accuracy: 83.59042553191489%
___________________________________________________________


In [ ]:
LOSS_HIS_2, TRAIN_ACC_HIS_2, VAL_ACC_HIS_2 = train(model_1, train_loader, val_loader, epochs = 5, learning_rate = 3e-5, path = '/content/drive/MyDrive/Colab Notebooks/DS/best_model_V2.pth')

  0%|          | 0/265 [00:00<?, ?it/s]<ipython-input-19-0220c28d08bb>:45: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'targets': torch.tensor(label, dtype=torch.float)
  0%|          | 1/265 [00:02<10:45,  2.44s/it]

 - Train Accuracy - Batch: 96.875%
 - Loss - Batch: 0.08710857480764389


  1%|          | 2/265 [00:04<10:31,  2.40s/it]

 - Train Accuracy - Batch: 97.65625%
 - Loss - Batch: 0.0965091809630394


  1%|          | 3/265 [00:07<10:28,  2.40s/it]

...

 - Train Accuracy - Batch: 99.21875%
 - Loss - Batch: 0.02768913097679615


  9%|▊         | 23/265 [01:02<10:55,  2.71s/it]

 - Train Accuracy - Batch: 98.4375%
 - Loss - Batch: 0.0274900421500206


  9%|▊         | 23/265 [01:03<11:10,  2.77s/it]


KeyboardInterrupt: ignored

In [ ]:
LOSS_HIS_3, TRAIN_ACC_HIS_3, VAL_ACC_HIS_3 = train(model_conv, train_loader, val_loader, epochs = 10, learning_rate = 5e-6, path = '/content/drive/MyDrive/Colab Notebooks/DS/best_model.pth')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
  0%|          | 0/133 [00:00<?, ?it/s]<ipython-input-20-80821b06bb6a>:49: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'targets': torch.tensor(label, dtype=torch.float)


 - Train Accuracy - Batch: 94.140625%


  1%|          | 1/133 [00:07<16:44,  7.61s/it]

 - Loss - Batch: 0.6098216772079468
 - Train Accuracy - Batch: 95.3125%


  2%|▏         | 2/133 [00:12<13:12,  6.05s/it]

...

 - Loss - Batch: 0.5945379734039307
 - Train Accuracy - Batch: 94.921875%


 17%|█▋        | 23/133 [02:18<10:25,  5.69s/it]

 - Loss - Batch: 0.6023668646812439


 17%|█▋        | 23/133 [02:19<11:07,  6.07s/it]


KeyboardInterrupt: ignored

In [ ]:
LOSS_HIS_4, TRAIN_ACC_HIS_4, VAL_ACC_HIS_4 = train(model_0, train_loader, val_loader, epochs = 10, learning_rate = 5e-4, path = '/content/drive/MyDrive/Colab Notebooks/DS/best_model_MLP.pth')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
  0%|          | 0/133 [00:00<?, ?it/s]<ipython-input-18-80821b06bb6a>:49: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'targets': torch.tensor(label, dtype=torch.float)
  1%|          | 1/133 [00:08<18:41,  8.49s/it]

DDDDD:  torch.Size([256, 768])
 - Train Accuracy - Batch: 31.640625%
 - Loss - Batch: 1.1012237071990967


  2%|▏         | 2/133 [00:12<12:58,  5.94s/it]

DDDDD:  torch.Size([256, 768])
 - Train Accuracy - Batch: 30.859375%
 - Loss - Batch: 1.1030694246292114


  2%|▏         | 3/133 [00:16<10:53,  5.03s/it]

...

DDDDD:  torch.Size([256, 768])


 93%|█████████▎| 14/15 [01:02<00:04,  4.40s/it]

DDDDD:  torch.Size([256, 768])


100%|██████████| 15/15 [01:05<00:00,  4.34s/it]

DDDDD:  torch.Size([176, 768])
Validation Accuracy: 69.12234042553192%
___________________________________________________________


In [ ]:
LOSS_HIS_5, TRAIN_ACC_HIS_5, VAL_ACC_HIS_5 = train(model_0, train_loader, val_loader, epochs = 10, learning_rate = 5e-5, path = '/content/drive/MyDrive/Colab Notebooks/DS/best_model_MLP.pth')

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
  0%|          | 0/133 [00:00<?, ?it/s]<ipython-input-18-80821b06bb6a>:49: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'targets': torch.tensor(label, dtype=torch.float)
  1%|          | 1/133 [00:04<09:06,  4.14s/it]

DDDDD:  torch.Size([256, 768])
 - Train Accuracy - Batch: 67.96875%
 - Loss - Batch: 0.7254506945610046


  2%|▏         | 2/133 [00:11<13:39,  6.25s/it]

DDDDD:  torch.Size([256, 768])
 - Train Accuracy - Batch: 68.359375%
 - Loss - Batch: 0.6845743656158447


  2%|▏         | 3/133 [00:16<12:03,  5.56s/it]

...

DDDDD:  torch.Size([256, 768])
 - Train Accuracy - Batch: 72.65625%
 - Loss - Batch: 0.6852190494537354


 19%|█▉        | 25/133 [02:49<12:10,  6.77s/it]

DDDDD:  torch.Size([256, 768])
 - Train Accuracy - Batch: 74.609375%
 - Loss - Batch: 0.670299232006073


 19%|█▉        | 25/133 [02:53<12:31,  6.96s/it]


KeyboardInterrupt: ignored

## Train Ranking

In [ ]:
# Khởi tạo Dataset cho tập huấn luyện và tập validation
X_train_NOT_NEI = X_train.loc[X_train['verdict'] != 'NEI'][:5000]
X_val_NOT_NEI = X_val.loc[X_val['verdict'] != 'NEI']

first 5000

In [ ]:
PAIR_train = CreatePairPOS_NEG(X_train_NOT_NEI)
PAIR_val = CreatePairPOS_NEG(X_val_NOT_NEI)

Streaming output truncated to the last 5000 lines.
# 2546
# 2547
# 2548
# 2549
# 2550
# 2551
# 2552
# 2553
# 2554
# 2555
# 2556
# 2557
# 2558
# 2559
# 2560
# 2561
# 2562
# 2563
# 2564
# 2565
# 2566
# 2567
# 2568
# 2569
# 2570
# 2571
# 2572
# 2573
# 2574
# 2575
# 2576
# 2577
# 2578
# 2579
# 2580
# 2581
# 2582
# 2583
# 2584
# 2585
# 2586
# 2587
# 2588
# 2589
# 2590
# 2591
# 2592
# 2593
# 2594
# 2595
# 2596
# 2597
# 2598
# 2599
# 2600
# 2601
# 2602
# 2603
# 2604
# 2605
# 2606
# 2607
# 2608
# 2609
# 2610
# 2611
# 2612
# 2613
# 2614
# 2615
# 2616
# 2617
# 2618
# 2619
# 2620
# 2621
# 2622
# 2623
# 2624
# 2625
# 2626
# 2627
# 2628
# 2629
# 2630
# 2631
# 2632
# 2633
# 2634
# 2635
# 2636
# 2637
# 2638
# 2639
# 2640
# 2641
# 2642
# 2643
# 2644
# 2645
# 2646
# 2647
# 2648
# 2649
# 2650
# 2651
# 2652
# 2653
# 2654
# 2655
# 2656
# 2657
# 2658
# 2659
# 2660
# 2661
# 2662
# 2663
# 2664
# 2665
# 2666
# 2667
# 2668
# 2669
# 2670
# 2671
# 2672
# 2673
# 2674
# 2675
# 2676
# 2677
# 2678
# 2679
# 2680
# 26

In [ ]:
PAIR_train['POS'] = [arr.tolist() for arr in PAIR_train["POS"]]
PAIR_train['NEG'] = [arr.tolist() for arr in PAIR_train["NEG"]]
PAIR_train['mask_pos'] = [arr.tolist() for arr in PAIR_train["mask_pos"]]
PAIR_train['mask_neg'] = [arr.tolist() for arr in PAIR_train["mask_neg"]]

In [ ]:
with open('/content/drive/MyDrive/Colab Notebooks/DS/data/pairTrain.json', 'w') as f:
    # Sử dụng json.dump để lưu từ điển vào tệp
    json.dump(PAIR_train, f)

In [ ]:
PAIR_val['POS'] = [arr.tolist() for arr in PAIR_val["POS"]]
PAIR_val['NEG'] = [arr.tolist() for arr in PAIR_val["NEG"]]
PAIR_val['mask_pos'] = [arr.tolist() for arr in PAIR_val["mask_pos"]]
PAIR_val['mask_neg'] = [arr.tolist() for arr in PAIR_val["mask_neg"]]

In [ ]:
with open('/content/drive/MyDrive/Colab Notebooks/DS/data/pairVal.json', 'w') as f:
    # Sử dụng json.dump để lưu từ điển vào tệp
    json.dump(PAIR_val, f)

last 5000

In [ ]:
X_train_NOT_NEI_LAST = X_train.loc[X_train['verdict'] != 'NEI'][-5000:]

In [ ]:
PAIR_train_LAST = CreatePairPOS_NEG(X_train_NOT_NEI_LAST)

Streaming output truncated to the last 5000 lines.
# 7545
# 7546
# 7547
# 7548
# 7549
# 7550
# 7551
# 7552
# 7553
# 7554
# 7555
# 7556
# 7557
# 7558
# 7559
# 7560
# 7561
# 7562
# 7563
# 7564
# 7565
# 7566
# 7567
# 7568
# 7569
# 7570
# 7571
# 7572
# 7573
# 7574
# 7575
# 7576
# 7577
# 7578
# 7579
# 7580
# 7581
# 7582
# 7583
# 7584
# 7585
# 7586
# 7587
# 7588
# 7589
# 7590
# 7591
# 7592
# 7593
# 7594
# 7595
# 7596
# 7597
# 7598
# 7599
# 7600
# 7601
# 7602
# 7603
# 7604
# 7605
# 7606
# 7607
# 7608
# 7609
# 7610
# 7611
# 7612
# 7613
# 7614
# 7615
# 7616
# 7617
# 7618
# 7619
# 7620
# 7621
# 7622
# 7623
# 7624
# 7625
# 7626
# 7627
# 7628
# 7629
# 7630
# 7631
# 7632
# 7633
# 7634
# 7635
# 7636
# 7637
# 7638
# 7639
# 7640
# 7641
# 7642
# 7643
# 7644
# 7645
# 7646
# 7647
# 7648
# 7649
# 7650
# 7651
# 7652
# 7653
# 7654
# 7655
# 7656
# 7657
# 7658
# 7659
# 7660
# 7661
# 7662
# 7663
# 7664
# 7665
# 7666
# 7667
# 7668
# 7669
# 7670
# 7671
# 7672
# 7673
# 7674
# 7675
# 7676
# 7677
# 7678
# 7679
# 76

In [ ]:
PAIR_train_LAST['POS'] = [arr.tolist() for arr in PAIR_train_LAST["POS"]]
PAIR_train_LAST['NEG'] = [arr.tolist() for arr in PAIR_train_LAST["NEG"]]
PAIR_train_LAST['mask_pos'] = [arr.tolist() for arr in PAIR_train_LAST["mask_pos"]]
PAIR_train_LAST['mask_neg'] = [arr.tolist() for arr in PAIR_train_LAST["mask_neg"]]

In [ ]:
with open('/content/drive/MyDrive/Colab Notebooks/DS/data/pairTrainLAST.json', 'w') as f:
    # Sử dụng json.dump để lưu từ điển vào tệp
    json.dump(PAIR_train_LAST, f)

MIDDLE

In [ ]:
X_train_NOT_NEI_MIDDLE = X_train.loc[X_train['verdict'] != 'NEI'][5000:-5000]

In [ ]:
PAIR_train_MIDDLE = CreatePairPOS_NEG(X_train_NOT_NEI_MIDDLE)

Streaming output truncated to the last 5000 lines.
# 7621
# 7622
# 7623
# 7624
# 7625
# 7626
# 7627
# 7628
# 7629
# 7630
# 7631
# 7632
# 7633
# 7634
# 7635
# 7636
# 7637
# 7638
# 7639
# 7640
# 7641
# 7642
# 7643
# 7644
# 7645
# 7646
# 7647
# 7648
# 7649
# 7650
# 7651
# 7652
# 7653
# 7654
# 7655
# 7656
# 7657
# 7658
# 7659
# 7660
# 7661
# 7662
# 7663
# 7664
# 7665
# 7666
# 7667
# 7668
# 7669
# 7670
# 7671
# 7672
# 7673
# 7674
# 7675
# 7676
# 7677
# 7678
# 7679
# 7680
# 7681
# 7682
# 7683
# 7684
# 7685
# 7686
# 7687
# 7688
# 7689
# 7690
# 7691
# 7692
# 7693
# 7694
# 7695
# 7696
# 7697
# 7698
# 7699
# 7700
# 7701
# 7702
# 7703
# 7704
# 7705
# 7706
# 7707
# 7708
# 7709
# 7710
# 7711
# 7712
# 7713
# 7714
# 7715
# 7716
# 7717
# 7718
# 7719
# 7720
# 7721
# 7722
# 7723
# 7724
# 7725
# 7726
# 7727
# 7728
# 7729
# 7730
# 7731
# 7732
# 7733
# 7734
# 7735
# 7736
# 7737
# 7738
# 7739
# 7740
# 7741
# 7742
# 7743
# 7744
# 7745
# 7746
# 7747
# 7748
# 7749
# 7750
# 7751
# 7752
# 7753
# 7754
# 7755
# 77

In [ ]:
PAIR_train_MIDDLE['POS'] = [arr.tolist() for arr in PAIR_train_MIDDLE["POS"]]
PAIR_train_MIDDLE['NEG'] = [arr.tolist() for arr in PAIR_train_MIDDLE["NEG"]]
PAIR_train_MIDDLE['mask_pos'] = [arr.tolist() for arr in PAIR_train_MIDDLE["mask_pos"]]
PAIR_train_MIDDLE['mask_neg'] = [arr.tolist() for arr in PAIR_train_MIDDLE["mask_neg"]]

In [ ]:
with open('/content/drive/MyDrive/Colab Notebooks/DS/data/pairTrainMIDDLE.json', 'w') as f:
    # Sử dụng json.dump để lưu từ điển vào tệp
    json.dump(PAIR_train_MIDDLE, f)

Read

In [ ]:
import json

def doc_json(filename):
    with open(filename, 'r') as f:
        data = json.load(f)
    return data


In [ ]:
# Sử dụng hàm
dataPairTrain = doc_json('/content/drive/MyDrive/Colab Notebooks/DS/data/pairTrain.json')

In [ ]:
dataPairVal = doc_json('/content/drive/MyDrive/Colab Notebooks/DS/data/pairVal.json')

In [ ]:
dataPairTrainLast = doc_json('/content/drive/MyDrive/Colab Notebooks/DS/data/pairTrainLAST.json')

In [ ]:
def data_plus_dict(A, B):
    for key in A.keys():
        if key in B:
            A[key].extend(B[key])
    return A

# Sử dụng hàm


In [ ]:
PAIR_TRAIN = data_plus_dict(dataPairTrain, dataPairTrainLast)

In [ ]:
PAIR_TRAIN['POS'] = [np.array(arr) for arr in PAIR_TRAIN["POS"]]
PAIR_TRAIN['NEG'] = [np.array(arr) for arr in PAIR_TRAIN["NEG"]]
PAIR_TRAIN['mask_pos'] = [np.array(arr) for arr in PAIR_TRAIN["mask_pos"]]
PAIR_TRAIN['mask_neg'] = [np.array(arr) for arr in PAIR_TRAIN["mask_neg"]]



# dataPairTrainLast['POS'] = [np.array(arr) for arr in dataPairTrainLast["POS"]]
# dataPairTrainLast['NEG'] = [np.array(arr) for arr in dataPairTrainLast["NEG"]]
# dataPairTrainLast['mask_pos'] = [np.array(arr) for arr in dataPairTrainLast["mask_pos"]]
# dataPairTrainLast['mask_neg'] = [np.array(arr) for arr in dataPairTrainLast["mask_neg"]]

In [ ]:
dataPairVal['POS'] = [np.array(arr) for arr in dataPairVal["POS"]]
dataPairVal['NEG'] = [np.array(arr) for arr in dataPairVal["NEG"]]
dataPairVal['mask_pos'] = [np.array(arr) for arr in dataPairVal["mask_pos"]]
dataPairVal['mask_neg'] = [np.array(arr) for arr in dataPairVal["mask_neg"]]

In [ ]:
ranking_dataset = EvidenceDataset(PAIR_TRAIN)
val_ranking_dataset = EvidenceDataset(dataPairVal)

# Khởi tạo DataLoader cho tập huấn luyện và tập validation
ranking_loader = DataLoader(ranking_dataset, batch_size=16, shuffle=True)
val_ranking_loader = DataLoader(val_ranking_dataset, batch_size=16)

In [ ]:
dataPairTrainMIDDLE = doc_json('/content/drive/MyDrive/Colab Notebooks/DS/data/pairTrainMIDDLE.json')

In [ ]:
dataPairTrainMIDDLE = data_plus_dict(PAIR_TRAIN, dataPairTrainMIDDLE)

In [ ]:
dataPairTrainMIDDLE['POS'] = [np.array(arr) for arr in dataPairTrainMIDDLE["POS"]]
dataPairTrainMIDDLE['NEG'] = [np.array(arr) for arr in dataPairTrainMIDDLE["NEG"]]
dataPairTrainMIDDLE['mask_pos'] = [np.array(arr) for arr in dataPairTrainMIDDLE["mask_pos"]]
dataPairTrainMIDDLE['mask_neg'] = [np.array(arr) for arr in dataPairTrainMIDDLE["mask_neg"]]

In [ ]:
ranking_dataset_MIDDLE = EvidenceDataset(dataPairTrainMIDDLE)
data_val = EvidenceDataset(dataPairVal)
# Khởi tạo DataLoader cho tập huấn luyện và tập validation
ranking_loader_MIDDLE = DataLoader(ranking_dataset_MIDDLE, batch_size=16, shuffle=True)
val_ranking_loader = DataLoader(data_val, batch_size=16)

In [ ]:
#97.17 train
#96.63 val

In [ ]:
save_path = '/content/drive/MyDrive/Colab Notebooks/DS/best_model_RANKING.pth'
LOSS_HIS_RANKING, TRAIN_ACC_HIS_RANKING, VAL_ACC_HIS_RANKING = ranking_learning(ranking_model, ranking_loader_MIDDLE, val_ranking_loader, save_path, epochs = 3, learning_rate = 1e-4)

  0%|          | 1/3182 [00:01<1:12:26,  1.37s/it]

 - Train Accuracy - Batch: 93.75%
 - Loss - Batch: 0.10221269726753235


  0%|          | 2/3182 [00:02<1:11:03,  1.34s/it]

 - Train Accuracy - Batch: 68.75%
 - Loss - Batch: 0.2666968107223511


  0%|          | 3/3182 [00:04<1:10:38,  1.33s/it]

...

 - Train Accuracy - Batch: 37.5%
 - Loss - Batch: 0.6999701857566833


 84%|████████▎ | 2663/3182 [1:02:33<12:09,  1.41s/it]

 - Train Accuracy - Batch: 37.5%
 - Loss - Batch: 0.6935230493545532


 84%|████████▎ | 2664/3182 [1:02:34<12:08,  1.41s/it]

 - Train Accuracy - Batch: 62.5%
 - Loss - Batch: 0.688578724861145


In [ ]:
LOSS_HIS_RANKING_1, TRAIN_ACC_HIS_RANKING_1, VAL_ACC_HIS_RANKING_1 = ranking_learning(ranking_model, ranking_loader_MIDDLE, val_ranking_loader, save_path, epochs = 3, learning_rate = 1e-4)

NameError: ignored

### FindEvidence_V2

In [ ]:
_,_,_,_,topD = FindEvidence_V2(df.loc[8280])
topD

# 1


{'Trong số 2.050 chỉ tiêu tuyển sinh trình độ đại học chính quy, 97,85% số thí sinh nhập học': tensor(5.7022, device='cuda:0'),
 'Tỷ lệ nhập học theo phương thức này chiếm khoảng 2% tổng số thí sinh nhập học của tất cả phương thức': tensor(3.2152, device='cuda:0'),
 'Theo thống kê của Bộ Giáo dục và Đào tạo, năm 2022, các trường dành hơn 30.000 chỉ tiêu xét tuyển từ điểm của các kỳ thi đánh giá năng lực, đánh giá tư duy': tensor(2.0546, device='cuda:0'),
 'Ngoài ra, các trường công an còn hai phương thức xét tuyển khác là tuyển thẳng theo quy định của Bộ Giáo dục và Đào tạo và xét tuyển kết hợp chứng chỉ tiếng Anh quốc tế': tensor(0.9546, device='cuda:0'),
 'Tại Hội nghị tổng kết công tác tuyển sinh năm 2022 và triển khai công tác tuyển sinh năm 2023 trong Công an nhân dân, sáng 8/3, Thiếu tướng, PGS.TS Đỗ Anh Tuấn, Cục trưởng Cục Đào tạo, cho biết năm nay Bộ Công an tiếp tục tổ chức kỳ thi đánh giá tuyển sinh': tensor(0.8104, device='cuda:0')}

In [ ]:
_,_,_,_,to = FindEvidence(df.loc[8280])
to

# 2


{'Tỷ lệ nhập học theo phương thức này chiếm khoảng 2% tổng số thí sinh nhập học của tất cả phương thức': tensor(3.2042, device='cuda:0'),
 'Theo thống kê của Bộ Giáo dục và Đào tạo, năm 2022, các trường dành hơn 30.000 chỉ tiêu xét tuyển từ điểm của các kỳ thi đánh giá năng lực, đánh giá tư duy': tensor(2.0543, device='cuda:0'),
 'Trong số 2.050 chỉ tiêu tuyển sinh trình độ đại học chính quy, 97,85% số thí sinh nhập học': tensor(1.7139, device='cuda:0'),
 'Ngoài ra, các trường công an còn hai phương thức xét tuyển khác là tuyển thẳng theo quy định của Bộ Giáo dục và Đào tạo và xét tuyển kết hợp chứng chỉ tiếng Anh quốc tế': tensor(0.9543, device='cuda:0'),
 'Tại Hội nghị tổng kết công tác tuyển sinh năm 2022 và triển khai công tác tuyển sinh năm 2023 trong Công an nhân dân, sáng 8/3, Thiếu tướng, PGS.TS Đỗ Anh Tuấn, Cục trưởng Cục Đào tạo, cho biết năm nay Bộ Công an tiếp tục tổ chức kỳ thi đánh giá tuyển sinh': tensor(0.8101, device='cuda:0')}

In [ ]:
def PrintErrorEvidencePredict_V2(df):
  score_true = 0
  # total = 0
  for i in range(len(df)):
    # total +=1
    _,_,_,_,a = FindEvidence_V2(df.iloc[i])
    if preprocess(list(a)[0]) != preprocess(df.iloc[i].evidence):
      score_true += 1
      print("CLAIM: ", df.iloc[i].claim)
      print("EVIDE: ", df.iloc[i].evidence)
      print("PREDI: ", a)
      print('___________________________________________________________________________________')

    print("CURRENT ERROR", score_true)
  print("FINALLY ERROR: ",score_true)
  return score_true

In [ ]:
# *1 ->126
# *2 -> 110
# *3 -> 97
# *3.5-> 97
# *4 -> 96

In [ ]:
!pip install python-Levenshtein


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 169.4/169.4 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 12.0 MB/s eta 0:00:00


In [ ]:
import Levenshtein as lev

def sentence_distance(sentence1, sentence2):
    words1 = sentence1.split()
    words2 = sentence2.split()
    score = 0
    total_distance = 0
    for word in words1:
      if word in words2:
        words2.remove(word)
        # print(words2)
        score += 1

    # print(words2)
    return score/len(words1)


In [ ]:
j = 'Học phí đối với sinh viên quốc tế của trường lên đến 4,5 tỷ đồng một năm'
g = 'Học phí đối với sinh viên quốc tế của trường dao động khoảng 50-100 triệu đồng một năm'
h = 'Học phí của Universidad Técnica Tederico Santa María (USM), Chile, trường đồng xếp hạng 386 với Đại học Quốc gia Hà Nội về ngành Kỹ thuật và Công nghệ, lên đến 4,5 tỷ đồng một năm'

In [ ]:
jaccard_similarity(j, h)

0.3

In [ ]:
jaccard_similarity(j,g)

0.5909090909090909

In [ ]:
jaccard_similarity(j, g)

0.5909090909090909

In [ ]:
jaccard_similarity(j, h)

0.3

In [ ]:
_,_,_,_,a = FindEvidence_V2(df.loc[14453])
a

# 7089


{'Học phí của Universidad Técnica Tederico Santa María (USM), Chile, trường đồng xếp hạng 386 với Đại học Quốc gia Hà Nội về ngành Kỹ thuật và Công nghệ, lên đến 4,5 tỷ đồng một năm': tensor(6.5162, device='cuda:0'),
 'Học phí đối với sinh viên quốc tế của trường dao động khoảng 50-100 triệu đồng một năm': tensor(6.2512, device='cuda:0'),
 'Nếu không theo diện học bổng, sinh viên quốc tế đến Bách khoa đóng học phí bằng 1,5 lần so với học phí của sinh viên Việt Nam, mức "tương đối dễ chịu so" với các nước': tensor(2.3829, device='cuda:0'),
 'Với Choi, nếu học ở Hàn Quốc cao, mỗi năm nam sinh này tốn khoảng 100 triệu đồng học phí, trong khi học phí ở Việt Nam bằng một nửa, 50,5 triệu đồng': tensor(2.0058, device='cuda:0'),
 'Theo PGS.TS Nguyễn Phong Điền, sinh viên quốc tế đến Bách khoa du học làm tăng thêm tầm ảnh hưởng và thương hiệu của trường trong bối cảnh hội nhập quốc tế': tensor(1.7508, device='cuda:0')}

In [ ]:
from sklearn.model_selection import train_test_split

yY = df['verdict']
# Train Test Split
X_T, X_V, y_T, y_V = train_test_split(
    df, yY, test_size=0.1, random_state=42)

In [ ]:
x_val_E = X_V.loc[X_V['verdict']!="NEI"]

In [ ]:
# 5 jac + 4 score ->98
# 30jac + 4 score ->99
# 25jac + 4 score ->99

In [ ]:
# 225 val
# 221 swap top 0.5
# 223 swap 1
# 222    swap 0.7
# 223 swap top 0.3

### Score

In [ ]:
PrintErrorEvidencePredict_V2(x_val_E)

Streaming output truncated to the last 5000 lines.
CURRENT ERROR 44
# 426
CURRENT ERROR 44
# 427
CURRENT ERROR 44
# 428
CURRENT ERROR 44
# 429
CURRENT ERROR 44
# 430
CURRENT ERROR 44
# 431
CURRENT ERROR 44
# 432
CURRENT ERROR 44
# 433
CURRENT ERROR 44
# 434
CURRENT ERROR 44
# 435
CURRENT ERROR 44
# 436
CURRENT ERROR 44
# 437
CURRENT ERROR 44
# 438
CURRENT ERROR 44
# 439
CURRENT ERROR 44
# 440
CURRENT ERROR 44
# 441
CURRENT ERROR 44
# 442
CURRENT ERROR 44
# 443
CURRENT ERROR 44
# 444
CURRENT ERROR 44
# 445
CURRENT ERROR 44
# 446
CURRENT ERROR 44
# 447
CURRENT ERROR 44
# 448
CURRENT ERROR 44
# 449
CURRENT ERROR 44
# 450
CURRENT ERROR 44
# 451
CURRENT ERROR 44
# 452
CURRENT ERROR 44
# 453
CURRENT ERROR 44
# 454
CURRENT ERROR 44
# 455
CURRENT ERROR 44
# 456
CURRENT ERROR 44
# 457
CURRENT ERROR 44
# 458
CLAIM:  Tỷ lệ bị lây nhiễm HBV từ mẹ của thai nhi tăng dần theo thời gian trong thai kì.
EVIDE:  

Bạn cần tiêm đủ 3 liều vaccine trong vòng 6 tháng sau theo lịch chỉ định của bác sĩ
PREDI: 

223

In [ ]:
PrintErrorEvidencePredict(x_val_E)

Streaming output truncated to the last 5000 lines.
# 5138
CURRENT ERROR 0.11764705882352941
# 5139
CURRENT ERROR 0.1174496644295302
# 5140
CURRENT ERROR 0.11725293132328309
# 5141
CURRENT ERROR 0.11705685618729098
# 5142
CURRENT ERROR 0.11686143572621036
# 5143
CURRENT ERROR 0.11666666666666667
# 5144
CURRENT ERROR 0.11647254575707154
# 5145
CURRENT ERROR 0.11627906976744186
# 5146
CURRENT ERROR 0.11608623548922056
# 5147
CURRENT ERROR 0.11589403973509933
# 5148
CURRENT ERROR 0.11570247933884298
# 5149
CURRENT ERROR 0.11551155115511551
# 5150
CURRENT ERROR 0.11532125205930807
# 5151
CURRENT ERROR 0.11513157894736842
# 5152
CURRENT ERROR 0.11494252873563218
# 5153
CURRENT ERROR 0.11475409836065574
# 5154
CLAIM:  Quã trình đã đạt được thành công ngoài mong đợi khi mở ra con người mới 
EVIDE:  "Quá trình này lập tức đi vào ngõ cụt".
INDEX:  Index(['context', 'claim', 'verdict', 'evidence', 'domain'], dtype='object')
PREDI:  {'Tuy nhiên, sau khi Nga bị cáo buộc gây ra vụ "thảm sát" ở thành

283

In [ ]:
def ScoreEvidencePredict(df):
  score_true = 0
  for i in range(len(df)):
    _,_,_,_,a = FindEvidence_V2(df.iloc[i])
    if preprocess(list(a)[0]) == preprocess(df.iloc[i].evidence):
      score_true += 1
    print("CURRENT SCORE", score_true)
  print("FINALLY SCORE: ",score_true)
  return score_true

In [ ]:
ScoreEvidencePredict(df)

# Testing

In [ ]:
df_test = pd.read_json("/content/drive/MyDrive/Colab Notebooks/DS/data/ise-dsc01-private-test-offcial.json", orient='index')

In [ ]:
model_conv = CNN()
checkpoint = torch.load('/content/drive/MyDrive/Colab Notebooks/DS/best_model_V2.pth')
model_conv.load_state_dict(checkpoint['model_state_dict'])

<All keys matched successfully>

In [ ]:
model_conv = model_conv.to(device)

In [ ]:
class Text_Test_Dataset(Dataset):
    def __init__(self, data_test):
        self.data_test = data_test
        self.max_len = 250

    def __len__(self):
        return len(self.data_test)

    def __getitem__(self, idx):
        context = self.data_test.iloc[idx]['context']
        claim = self.data_test.iloc[idx]['claim']
        id = self.data_test.index[idx]

        _, _, _, _, cand = FindEvidence_V2(self.data_test.iloc[idx])
        evidence = list(cand)[0]
        evidence_pro = preprocess_text(evidence)
        s1 = preprocess(claim)
        s2 = preprocess(evidence)

        line_1 = underthesea.word_tokenize(s1, format="text")
        line_2 = underthesea.word_tokenize(s2, format="text")

        # Tokenize câutokenizer_phobert_v2.encode(line)
        s1_tokenized = tokenizer_phobert_v2.encode(line_1, add_special_tokens=True)
        s2_tokenized = tokenizer_phobert_v2.encode(line_2, add_special_tokens=True)[1:]

        v_tokenized = s1_tokenized + s2_tokenized

        # Chèn thêm số 1 vào cuối câu nếu như không đủ 200 từ
        padded = numpy.array([v_tokenized + [1] * (self.max_len - len(v_tokenized))])
        attention_mask = numpy.where(padded == 1, 0, 1)

        padded = torch.tensor(padded).to(torch.long)
        attention_mask = torch.tensor(attention_mask)

        padded = padded.to(device)
        attention_mask = attention_mask.to(device)

        with torch.no_grad():
          outputs = phobert_v2(input_ids = padded, attention_mask = attention_mask)

        v_features = outputs[2]


        return {
            'outputs': v_features,
            'evidence': evidence_pro,
            'id': id
        }

In [ ]:
def create_dict(ids, verdicts, evidences):
    return {id: {'verdict': verdict, 'evidence': evidence} for id, verdict, evidence in zip(ids, verdicts, evidences)}

def add_to_dict(main_dict, new_dict):
    for key, value in new_dict.items():
        if key not in main_dict:
            main_dict[key] = value
        else:
            main_dict[key]['verdict'].extend(value['verdict'])
            main_dict[key]['evidence'].extend(value['evidence'])
    return main_dict

# # ví dụ
# main_dict = {}
# ids = ['id1', 'id2', 'id3']
# verdicts = ['verdict1', 'verdict2', 'verdict3']
# evidences = ['evidence1', 'evidence2', 'evidence3']

# new_dict = create_dict(ids, verdicts, evidences)
# main_dict = add_to_dict(main_dict, new_dict)

# print(main_dict)


In [ ]:
def test(model, test_loader):
  evidence = []
  verdict = []
  # result = {}
  index = []
  model.eval()
  with torch.no_grad():
      for batch in tqdm(test_loader):
          input = batch['outputs']
          evidence_pre = batch['evidence']
          id = batch['id']

          outputs = model(input)
          # print('Output = ',outputs)
          predicted = outputs.argmax(dim=1)
          predicted_label = encoder.inverse_transform(list(predicted.cpu()))
          # print('Predicted Label', predicted_label)
          verdict.extend(predicted_label)
          index.extend(id)
          evidence.extend(evidence_pre)

  result = create_dict(index, verdict, evidence)

  return result

In [ ]:
X_test_input_data = df_test

test_dataset = Text_Test_Dataset(X_test_input_data)

test_loader = DataLoader(test_dataset, batch_size=128)

In [ ]:
dict_result = test(model_conv, test_loader)

  0%|          | 0/43 [00:00<?, ?it/s]

# 2
# 3
# 4
# 5
# 6
# 7
# 8
# 9
# 10
# 11
# 12
# 13
# 14
# 15
# 16
# 17
# 18
# 19
# 20
# 21
# 22
# 23
# 24
# 25
# 26
# 27
# 28
# 29
# 30
# 31
# 32
# 33
# 34
# 35
# 36
# 37
# 38
# 39
# 40
# 41
# 42
# 43
# 44
# 45
# 46
# 47
# 48
# 49
# 50
# 51
# 52
# 53
# 54
# 55
# 56
# 57
# 58
# 59
# 60
# 61
# 62
# 63
# 64
# 65
# 66
# 67
# 68
# 69
# 70
# 71
# 72
# 73
# 74
# 75
# 76
# 77
# 78
# 79
# 80
# 81
# 82
# 83
# 84
# 85
# 86
# 87
# 88
# 89
# 90
# 91
# 92
# 93
# 94
# 95
# 96
# 97
# 98
# 99
# 100
# 101
# 102
# 103
# 104
# 105
# 106
# 107
# 108
# 109
# 110
# 111
# 112
# 113
# 114
# 115
# 116
# 117
# 118
# 119
# 120
# 121
# 122
# 123
# 124
# 125
# 126
# 127
# 128
# 129


  2%|▏         | 1/43 [01:04<45:01, 64.31s/it]

# 130
# 131
# 132
# 133
# 134
# 135
# 136
# 137
# 138
# 139
# 140
# 141
# 142
# 143
# 144
# 145
# 146
# 147
# 148
# 149
# 150
# 151
# 152
# 153
# 154
# 155
# 156
# 157
# 158
# 159
# 160
# 161
# 162
# 163
# 164
# 165
# 166
# 167
# 168
# 169
# 170
# 171
# 172
# 173
# 174
# 175
# 176
# 177
# 178
# 179
# 180
# 181
# 182
# 183
# 184
# 185
# 186
# 187
# 188
# 189
# 190
# 191
# 192
# 193
# 194
# 195
# 196
# 197
# 198
# 199
# 200
# 201
# 202
# 203
# 204
# 205
# 206
# 207
# 208
# 209
# 210
# 211
# 212
# 213
# 214
# 215
# 216
# 217
# 218
# 219
# 220
# 221
# 222
# 223
# 224
# 225
# 226
# 227
# 228
# 229
# 230
# 231
# 232
# 233
# 234
# 235
# 236
# 237
# 238
# 239
# 240
# 241
# 242
# 243
# 244
# 245
# 246
# 247
# 248
# 249
# 250
# 251
# 252
# 253
# 254
# 255
# 256
# 257


  5%|▍         | 2/43 [01:34<30:03, 43.99s/it]

...

 95%|█████████▌| 41/43 [20:56<00:59, 29.50s/it]

# 5250
# 5251
# 5252
# 5253
# 5254
# 5255
# 5256
# 5257
# 5258
# 5259
# 5260
# 5261
# 5262
# 5263
# 5264
# 5265
# 5266
# 5267
# 5268
# 5269
# 5270
# 5271
# 5272
# 5273
# 5274
# 5275
# 5276
# 5277
# 5278
# 5279
# 5280
# 5281
# 5282
# 5283
# 5284
# 5285
# 5286
# 5287
# 5288
# 5289
# 5290
# 5291
# 5292
# 5293
# 5294
# 5295
# 5296
# 5297
# 5298
# 5299
# 5300
# 5301
# 5302
# 5303
# 5304
# 5305
# 5306
# 5307
# 5308
# 5309
# 5310
# 5311
# 5312
# 5313
# 5314
# 5315
# 5316
# 5317
# 5318
# 5319
# 5320
# 5321
# 5322
# 5323
# 5324
# 5325
# 5326
# 5327
# 5328
# 5329
# 5330
# 5331
# 5332
# 5333
# 5334
# 5335
# 5336
# 5337
# 5338
# 5339
# 5340
# 5341
# 5342
# 5343
# 5344
# 5345
# 5346
# 5347
# 5348
# 5349
# 5350
# 5351
# 5352
# 5353
# 5354
# 5355
# 5356
# 5357
# 5358
# 5359
# 5360
# 5361
# 5362
# 5363
# 5364
# 5365
# 5366
# 5367
# 5368
# 5369
# 5370
# 5371
# 5372
# 5373
# 5374
# 5375
# 5376
# 5377


 98%|█████████▊| 42/43 [21:25<00:29, 29.49s/it]

# 5378
# 5379
# 5380
# 5381
# 5382
# 5383
# 5384
# 5385
# 5386
# 5387
# 5388
# 5389
# 5390
# 5391
# 5392
# 5393
# 5394
# 5395
# 5396
# 5397


100%|██████████| 43/43 [21:30<00:00, 30.02s/it]


In [ ]:
########################################
# Giả sử rằng `dict_result` là từ điển bạn muốn chỉnh sửa
for key in dict_result.keys():
    if dict_result[key]['verdict'] == 'NEI':
        dict_result[key]['evidence'] = ""


In [ ]:
# Giả sử rằng `dict_result` là từ điển bạn muốn chuyển đổi thành JSON
for key in list(dict_result.keys()):  # Tạo một bản sao của các khóa
    if isinstance(key, torch.Tensor):
        # Chuyển đổi tensor thành số nếu nó chỉ có một phần tử
        if key.numel() == 1:
            new_key = key.item()
        # Nếu không, chuyển đổi tensor thành danh sách
        else:
            new_key = key.tolist()
        # Cập nhật từ điển với khóa mới
        dict_result[new_key] = dict_result.pop(key)


In [ ]:
dict_result

{39773: {'verdict': 'NEI', 'evidence': ''},
 37657: {'verdict': 'REFUTED',
  'evidence': 'một số người khuyên em theo công nghệ thực phẩm thay vì công nghệ dệt may nhưng em ghét hóa'},
 40265: {'verdict': 'NEI', 'evidence': ''},
 47711: {'verdict': 'REFUTED',
  'evidence': 'nhãn hàng sẽ cùng đối tác đề ra những chiến lược phát triển kinh doanh đem lại sản phẩm chất lượng cho thị trường'},
 39930: {'verdict': 'REFUTED',
  'evidence': 'chúng tôi gọi đó là bụi thông minh và chỉ vài tế bào vi khuẩn cũng có thể tạo ra đủ năng lượng cho chúng'},
 37208: {'verdict': 'SUPPORTED',
  'evidence': 'người mắc bệnh phổi tắc nghẽn mạn tính hen suyễn bệnh màng phổi hội chứng giảm thông khí ngưng thở khi ngủ'},
 38194: {'verdict': 'REFUTED',
  'evidence': 'cdc khuyến nghị người trưởng thành người già và những người dễ mắc covid19 vẫn tiêm chủng đầy đủ theo lịch trình trước đó'},
 42930: {'verdict': 'SUPPORTED',
  'evidence': 'ngoài ra hiu cũng công bố chương trình học bổng doanh nghiệp đồng hành 2023'}

In [ ]:
# Sử dụng 'utf-8' để không mã hóa các kí tự đặc biệt
with open('/content/drive/MyDrive/Colab Notebooks/DS/data/private_result.json', 'w', encoding='utf-8') as f:
    json.dump(dict_result, f, ensure_ascii=False, indent=4)

In [ ]:
# a= "Video được đăng trên mạng xã hội Trung Quốc tuần qua cho thấy bé gái ở tỉnh Cát Lâm, đông bắc nước này, đứng cạnh chiếc bàn trong phòng khách, cười tươi khi được bố trao một hộp quà mừng sinh nhật được bọc cẩn thận."
# b= "Video được đăng trên mạng xã hội Trung Quốc tuần qua cho thấy bé gái ở tỉnh Cát Lâm, đông bắc nước này, đứng cạnh chiếc bàn trong phòng khách, cười tươi khi được bố trao một hộp \"quà bất ngờ\" được bọc cẩn thận."
# test(model_DNN, a, b)

In [ ]:
# i={   "16473": {
#         "context": "Video được đăng trên mạng xã hội Trung Quốc tuần qua cho thấy bé gái ở tỉnh Cát Lâm, đông bắc nước này, đứng cạnh chiếc bàn trong phòng khách, cười tươi khi được bố trao một hộp \"quà bất ngờ\" được bọc cẩn thận.\n\n\"Đây là quà bố tặng con đấy, con có vui không?\", người mẹ vừa hỏi vừa quay video. \"Con vui ạ\", cô bé trả lời và cảm ơn bố, trên gương mặt lộ rõ vẻ háo hức.\n\nNhưng sau khi mở hộp, bé gái phát hiện \"món quà\" bên trong lại là một cuốn sách bài tập màu vàng. \"Cái gì thế này? Sao bố lại mua tặng con sách bài tập\", bé vừa hỏi vừa lật giở từng trang sách.\n\nNgười mẹ phá lên cười và nhắc con gái rằng đó là một món quà. Bé gái không nói gì nữa, gấp quyển sách lại và biểu cảm buồn bã xuất hiện trên gương mặt. \"Đó mà là quà sao\", cô bé hỏi.\n\nBé sau đó ném cuốn sách về phía mẹ, rồi tiếp tục lật chiếc hộp để xem còn thứ gì bên trong không. \"Chỉ còn mỗi xốp thôi\", bé vừa nói vừa khóc.\n\nSau khi được chia sẻ trên mạng xã hội Trung Quốc, video đã gây nhiều tranh luận. Nhiều người cho rằng bố mẹ cô bé đã đối xử tàn nhẫn với con, khi khiến bé hy vọng về một món quà, nhưng rốt cuộc chỉ nhận được cuốn sách bài tập.\n\n\"Cô bé khóc vì bất bình. Sao người bố có thể làm thế với cô con gái đáng yêu như vậy cơ chứ?\", một người bình luận.\n\nMột số người không vui vì hành động ném cuốn sách của cô bé, nhưng cho rằng người mẹ không tinh tế khi cười to trước nỗi thất vọng của con.",
#         "claim": "Video được đăng trên mạng xã hội Trung Quốc tuần qua cho thấy bé gái ở tỉnh Cát Lâm, đông bắc nước này, đứng cạnh chiếc bàn trong phòng khách, cười tươi khi được bố trao một hộp quà mừng sinh nhật được bọc cẩn thận.",
#         "verdict": "REFUTED",
#         "evidence": "Video được đăng trên mạng xã hội Trung Quốc tuần qua cho thấy bé gái ở tỉnh Cát Lâm, đông bắc nước này, đứng cạnh chiếc bàn trong phòng khách, cười tươi khi được bố trao một hộp \"quà bất ngờ\" được bọc cẩn thận.",
#         "domain": "the-gioi"
#     }}
# d = pd.DataFrame.from_dict(i, orient='index')

In [ ]:
# print(d['verdict'])

In [ ]:
# i = {
#     "16473": {
#         "context": "...",
#         "claim": "...",
#         "verdict": "REFUTED",
#         "evidence": "...",
#         "domain": "the-gioi"
#     }
# }

# Chuyển đổi dictionary sang DataFrame
# df = pd.DataFrame.from_dict(i, orient='index')

# print(df)

In [ ]:
# df.iloc[0]

In [ ]:
# _,_,_,_,eee = FindEvidence(d.iloc[0], thres_value=None, top=4)

In [ ]:
# X_train.loc[X_train['verdict']!='NEI'][:10]